In [2]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
import optuna
import torch
import tensorflow as tf
from tensorflow import feature_column
from tensorflow.keras import layers
from tqdm.auto import tqdm
from pytorch_tabnet.tab_model import TabNetRegressor
from sklearn.model_selection import KFold
from sklearn.model_selection import cross_validate
from sklearn.ensemble import VotingClassifier
from sklearn.ensemble import VotingRegressor
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import RobustScaler
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer
from sklearn.decomposition import PCA

In [3]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

In [4]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10   X_11   X_12  \
0     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
1     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
2     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
3     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
4     NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
..    ...   ...  ...   ...   ...  ...   ...   ...   ...   ...    ...    ...   
593   2.0  95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  468.9  473.9   
594   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
595   NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN   NaN   NaN    NaN    NaN   
596  40.0  94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  505.8  510.9   
597  21.0  87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  470.6  474.9   

      X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20   X_21   X_22  X_23  \
0      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...   ...   ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  459.2   0.0   0.0  247.5  248.0  247.3  250.0  527.0  538.0  522.0  0.19   
594    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  497.1   0.0   0.0  247.5  248.1  247.3  250.0  489.0  498.0  485.0  0.19   
597  462.9   0.0   0.0  247.5  248.0  247.3  250.0  525.0  534.0  520.0  0.19   

     X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31   X_32   X_33  \
0     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
1     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
2     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
3     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
4     NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
..    ...   ...    ...    ...    ...    ...    ...    ...    ...    ...   
593  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
594   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
595   NaN   NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   
596  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   
597  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0  185.0  185.0   

      X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  X_43  X_44  \
0      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2      NaN

In [5]:
train_data['YEAR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.year
train_data['MONTH'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.month
train_data['DAY'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day
train_data['HOUR'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.hour
train_data['MINUTE'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.minute
train_data['DAY_OF_WEEK'] =  pd.to_datetime(train_data['TIMESTAMP']).dt.day_name()

In [6]:
train_data = train_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [7]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [8]:
train_data.drop(colls, inplace = True, axis = 1)

In [9]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.loc[train_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
train_data.loc[train_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
train_data.loc[train_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
train_data.loc[train_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
train_data.loc[train_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
train_data.loc[train_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
train_data.loc[train_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

train_data.drop(['PRODUCT_ID', 'TIMESTAMP', 'PRODUCT_CODE'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE   X_1   X_2  X_3   X_4   X_5  X_6   X_7  \
0          1   0.533433  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
1          2   0.541819  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
2          1   0.531267  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
3          2   0.537325  T050307   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
4          1   0.531590  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
..       ...        ...      ...   ...   ...  ...   ...   ...  ...   ...   
593        1   0.526546  T100306   2.0  95.0  0.0  45.0  10.0  0.0  50.0   
594        0   0.524022  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
595        0   0.521289  T050304   NaN   NaN  NaN   NaN   NaN  NaN   NaN   
596        1   0.531375  T100304  40.0  94.0  0.0  45.0  11.0  0.0  45.0   
597        1   0.533702  T100306  21.0  87.0  0.0  45.0  10.0  0.0  61.0   

      X_8   X_9  X_10   X_11   X_12   X_13  X_14  X_15   X_16   X_17   X_18  \
0     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
1     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
2     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
3     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
4     NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
..    ...   ...   ...    ...    ...    ...   ...   ...    ...    ...    ...   
593  10.0  52.0   2.0  468.9  473.9  459.2   0.0   0.0  247.5  248.0  247.3   
594   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
595   NaN   NaN   NaN    NaN    NaN    NaN   NaN   NaN    NaN    NaN    NaN   
596  10.0  31.0   2.0  505.8  510.9  497.1   0.0   0.0  247.5  248.1  247.3   
597  10.0  52.0   2.0  470.6  474.9  462.9   0.0   0.0  247.5  248.0  247.3   

      X_19   X_20   X_21   X_22  X_23  X_24  X_25   X_26   X_27   X_28   X_29  \
0      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
1      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
2      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
3      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
4      NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
..     ...    ...    ...    ...   ...   ...   ...    ...    ...    ...    ...   
593  250.0  527.0  538.0  522.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0   
594    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
595    NaN    NaN    NaN    NaN   NaN   NaN   NaN    NaN    NaN    NaN    NaN   
596  250.0  489.0  498.0  485.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0   
597  250.0  525.0  534.0  520.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0   

      X_30   X_31   X_32   X_33   X_34   X_35   X_36   X_37   X_38  X_39  \
0      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
1      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
2      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
3      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
4      NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...   ...   
593  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0   
594    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
595    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN    NaN   NaN   
596  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.078   1.0   
597  185.0  185.0  185.0  185.0  155.0  155.0  155.0  155.0  0.077   1.0   

     X_40  X_41  X_42  X_43  X_44  X_45  X_46  X_47  X_48  X_49  X_50  X_51  \
0     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
1     NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   
2     NaN   NaN   Na

In [10]:
T050304 = train_data[train_data['LINE'] == 'T050304']
T050307 = train_data[train_data['LINE'] == 'T050307']
T010305 = train_data[train_data['LINE'] == 'T010305']
T010306 = train_data[train_data['LINE'] == 'T010306']
T100304 = train_data[train_data['LINE'] == 'T100304']
T100306 = train_data[train_data['LINE'] == 'T100306']

In [11]:
T050304.drop(['LINE'], axis = 1, inplace = True)
T050307.drop(['LINE'], axis = 1, inplace = True)
T010305.drop(['LINE'], axis = 1, inplace = True)
T010306.drop(['LINE'], axis = 1, inplace = True)
T100304.drop(['LINE'], axis = 1, inplace = True)
T100306.drop(['LINE'], axis = 1, inplace = True)

In [12]:
T050304_col = []
for col in T050304 :
    if 'X' in col and T050304[col].isna().sum() == len(T050304) :
        T050304_col.append(col)
print(len(T050304_col))

T050304.drop(T050304_col, inplace = True, axis = 1)

825


In [13]:
T050307_col = []
for col in T050307 :
    if 'X' in col and T050307[col].isna().sum() == len(T050307) :
        T050307_col.append(col)
print(len(T050307_col))

T050307.drop(T050307_col, inplace = True, axis = 1)

818


In [14]:
T010305_col = []
for col in T010305 :
    if 'X' in col and T010305[col].isna().sum() == len(T010305) :
        T010305_col.append(col)
print(len(T010305_col))

T010305.drop(T010305_col, inplace = True, axis = 1)

1907


In [15]:
T010306_col = []
for col in T010306 :
    if 'X' in col and T010306[col].isna().sum() == len(T010306) :
        T010306_col.append(col)
print(len(T010306_col))

T010306.drop(T010306_col, inplace = True, axis = 1)

1907


In [16]:
T100304_col = []
for col in T100304 :
    if 'X' in col and T100304[col].isna().sum() == len(T100304) :
        T100304_col.append(col)
print(len(T100304_col))

T100304.drop(T100304_col, inplace = True, axis = 1)

2122


In [17]:
T100306_col = []
for col in T100306 :
    if 'X' in col and T100306[col].isna().sum() == len(T100306) :
        T100306_col.append(col)
print(len(T100306_col))

T100306.drop(T100306_col, inplace = True, axis = 1)

2122


In [18]:
T051 = list(set(T050307_col)-set(T050304_col))
T052 = list(set(T050304_col)-set(T050307_col))
T5drop = T051 + T052

T011 = list(set(T010305_col)-set(T010306_col))
T012 = list(set(T010306_col)-set(T010305_col))
T0drop = T011 + T012

T101 = list(set(T100304_col)-set(T100306_col))
T102 = list(set(T100306_col)-set(T100304_col))
T1drop = T101 + T102

In [19]:
T05 = pd.concat([T050304, T050307])
T01 = pd.concat([T010305, T010306])
T10 = pd.concat([T100304, T100306])

In [20]:
T05.drop(T5drop, inplace = True, axis = 1)
T01.drop(T0drop, inplace = True, axis = 1)
T10.drop(T1drop, inplace = True, axis = 1)

In [21]:
T05

Y_Class  Y_Quality  X_132  X_133  X_134  X_135  X_136  X_137  X_138  \
0          1   0.533433   0.19    0.2   0.19    0.2  228.0  228.0  225.0   
2          1   0.531267   0.19    0.2   0.19    0.2  228.0  228.0  225.0   
4          1   0.531590   0.19    0.2   0.18    0.2  228.0  228.0  225.0   
6          1   0.533665   0.19    0.2   0.19    0.2  228.0  228.0  225.0   
8          1   0.531821   0.19    0.2   0.19    0.2  228.0  228.0  225.0   
..       ...        ...    ...    ...    ...    ...    ...    ...    ...   
549        1   0.533711   0.19    0.2   0.19    0.2   81.0   81.0   81.0   
550        1   0.533695   0.19    0.2   0.19    0.2   82.0   82.0   82.0   
551        1   0.525271   0.19    0.2   0.19    0.2   84.0   84.0   84.0   
552        1   0.529806   0.19    0.2   0.19    0.2   84.0   84.0   84.0   
555        0   0.521406   0.19    0.2   0.19    0.2   87.0   87.0   87.0   

     X_139  X_140  X_141  X_142  X_143   X_144   X_145   X_146  X_147  X_148  \
0    582.9  587.1  567.3    0.0    0.0  249.96  249.99  247.46  250.0  428.0   
2    583.8  587.6  572.9    0.0    0.0  249.97  249.99  249.10  250.0  427.0   
4    583.2  587.3  565.9    0.0    0.0  249.96  249.99  246.46  250.0  428.0   
6    583.4  587.3  543.9    0.0    0.0  249.95  249.99  235.56  250.0  428.0   
8    583.3  587.2  571.9    0.0    0.0  249.97  249.99  248.96  250.0  428.0   
..     ...    ...    ...    ...    ...     ...     ...     ...    ...    ...   
549  564.3  568.8  549.6    0.0    0.0  249.97  249.99  248.55  250.0  442.0   
550  564.3  568.6  549.0    0.0    0.0  249.96  249.99  247.93  250.0  442.0   
551  564.4  568.7  553.5    0.0    0.0  249.97  249.99  249.26  250.0  442.0   
552  564.6  568.9  549.2    0.0    0.0  249.97  249.99  247.93  250.0  442.0   
555  563.7  568.9  542.6    0.0    0.0  249.96  249.99  244.94  250.0  443.0   

     X_149  X_150  X_151  X_152  X_153  X_154  X_155  X_156  X_157  X_158  \
0    435.0  426.0  179.9  180.0  179.9  180.0  215.0  215.0  214.9  215.0   
2    434.0  425.0  179.9  180.0  179.8  180.0  215.0  215.0  214.9  215.0   
4    434.0  426.0  180.0  180.0  179.8  180.0  215.0  215.1  215.0  215.0   
6    434.0  425.0  180.0  180.1  179.9  180.0  214.9  215.0  214.9  215.0   
8    434.0  426.0  180.0  180.0  179.9  180.0  215.0  215.0  214.9  215.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549  450.0  439.0  179.9  180.0  179.7  180.0  215.0  215.0  214.9  215.0   
550  450.0  439.0  180.0  180.0  179.9  180.0  215.0  215.0  214.9  215.0   
551  450.0  439.0  179.9  180.0  179.8  180.0  214.9  215.0  214.9  215.0   
552  450.0  439.0  179.9  179.9  179.8  180.0  215.0  215.0  214.8  215.0   
555  451.0  439.0  180.0  180.0  179.9  180.0  214.9  215.0  214.9  215.0   

     X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  X_167  X_168  \
0    214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9  210.0   
2    215.0  215.0  214.9  215.0  209.9  210.0  209.9  210.0  209.9  210.0   
4    214.9  215.0  214.9  215.0  210.0  210.1  210.0  210.0  209.9  210.0   
6    215.0  215.0  214.9  215.0  210.0  210.0  209.9  210.0  210.0  210.0   
8    215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0  210.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549  214.9  215.0  214.9  215.0  209.9  210.0  209.9  210.0  210.0  210.0   
550  215.0  215.0  214.9  215.0  210.0  210.1  210.0  210.0  210.0  210.0   
551  214.9  215.0  214.9  215.0  210.0  210.0  210.0  210.0  210.0  210.1   
552  214.9  215.1  214.9  215.0  209.9  210.0  209.9  210.0  210.0  210.0   
555  215.0  215.1  214.9  215.0  210.0  210.0  210.0  210.0  210.0  210.0   

     X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  X_177  X_178  \
0    209.9  210.0  205.0  205.0  204.9  205.0  204.9  205.0  204.9  205.0   
2    209.9  210.0  204.9  205.0  204.9  205.0  204.9  205.0  204.9  205.0   
4    209.9  210.0  204.9  205.0  204.9  205.0  204

In [22]:
T01

Y_Class  Y_Quality  X_246  X_247  X_248  X_249  X_250  X_251  X_252  \
28         0   0.521249    1.0   89.0    0.0   45.0   11.0   90.0   45.0   
33         1   0.526656    1.0   95.0    0.0   45.0   11.0   98.0   45.0   
39         1   0.531583    1.0   95.0    0.0   45.0   11.0  102.0   45.0   
40         1   0.530829    1.0   95.0    0.0   45.0   11.0  105.0   45.0   
41         1   0.528270    1.0   87.0    0.0   45.0   11.0  105.0   45.0   
..       ...        ...    ...    ...    ...    ...    ...    ...    ...   
479        1   0.534716    1.0   93.0  107.0   45.0   11.0    0.0   45.0   
501        1   0.533079    2.0   95.0  124.0   45.0   11.0    0.0   45.0   
523        1   0.534640    1.0   89.0  136.0   45.0   12.0    0.0   45.0   
531        2   0.560317    1.0   90.0  142.0   45.0   11.0    0.0   45.0   
585        0   0.515214    1.0   93.0   63.0   45.0   12.0    0.0   45.0   

     X_253  X_254  X_255  X_256  X_257  X_258  X_259  X_260  X_261  X_262  \
28    11.0   42.0    2.0  481.1  486.8  472.2    0.0    0.0  246.8  247.3   
33    11.0   42.0    2.0  481.4  488.3  471.2    0.0    0.0  246.7  247.2   
39    12.0   42.0    2.0  482.7  489.3  471.9    0.0    0.0  246.7  247.0   
40    11.0   42.0    2.0  485.0  491.7  473.4    0.0    0.0  247.1  247.7   
41    11.0   42.0    2.0  484.9  491.7  474.4    0.0    0.0  247.1  247.6   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479   12.0   51.0    2.0  485.8  492.9  476.1    0.0    0.0  246.6  247.7   
501   12.0   51.0    2.0  490.8  497.8  481.5    0.0    0.0  246.6  247.5   
523   12.0   51.0    2.0  494.4  502.1  484.9    0.0    0.0  246.6  247.7   
531   12.0   51.0    2.0  496.8  503.6  485.6    0.0    0.0  246.9  247.9   
585   12.0   51.0    2.0  480.5  485.9  473.4    0.0    0.0  246.3  247.4   

     X_263  X_264  X_265  X_266  X_267  X_268  X_269  X_270  X_271  X_272  \
28   246.2  250.0  510.0  520.0  505.0   0.20    0.2   0.20  150.0  150.0   
33   246.4  250.0  509.0  520.0  504.0   0.20    0.2   0.20  149.0  150.0   
39   246.2  250.0  508.0  520.0  501.0   0.20    0.2   0.20  149.0  150.0   
40   246.6  250.0  506.0  517.0  500.0   0.20    0.2   0.20  149.0  150.0   
41   246.9  250.0  506.0  518.0  500.0   0.20    0.2   0.20  149.0  150.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479  245.6  250.0  507.0  518.0  501.0   0.19    0.2   0.19  149.0  149.0   
501  246.0  250.0  502.0  514.0  495.0   0.19    0.2   0.19  149.0  150.0   
523  245.7  250.0  498.0  511.0  491.0   0.20    0.2   0.20  149.0  150.0   
531  245.9  250.0  497.0  508.0  489.0   0.19    0.2   0.19  149.0  150.0   
585  245.6  250.0  512.0  522.0  507.0   0.19    0.2   0.19  149.0  150.0   

     X_273  X_274  X_275  X_276  X_277  X_278  X_279  X_280  X_281  X_282  \
28   150.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0   
33   149.0  150.0  150.0  150.0  150.0  150.0  149.0  150.0  149.0  150.0   
39   149.0  150.0  150.0  150.0  150.0  150.0  149.0  150.0  149.0  150.0   
40   149.0  150.0  150.0  150.0  150.0  150.0  149.0  150.0  149.0  150.0   
41   149.0  150.0  150.0  150.0  150.0  150.0  150.0  150.0  150.0  150.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0   
501  149.0  150.0  150.0  150.0  150.0  150.0  149.0  150.0  149.0  150.0   
523  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0   
531  149.0  150.0  150.0  150.0  150.0  150.0  149.0  150.0  149.0  150.0   
585  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0  149.0  150.0   

     X_283  X_284  X_285  X_286  X_287  X_288  X_289  X_290  X_291  X_292  \
28   0.075    1.0   66.9   68.6   66.9   79.4   71.3   82.0   69.4   67.3   
33   0.075    1.0   66.9   68.6   66.9   79.4   71.3   82.0   69.4   67.3   
39   0.074    1.0   66.9   68.6   66.9   79.4   71.3   82.0   69.4   67.3   
40   0.07

In [23]:
T10

Y_Class  Y_Quality   X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  \
22         0   0.517719   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
23         0   0.519090   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
25         1   0.529362   2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
29         1   0.532405   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
37         1   0.533110   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   
..       ...        ...   ...    ...  ...   ...   ...  ...   ...   ...   ...   
589        1   0.529510   1.0   94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   
590        1   0.529948   1.0   89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   
591        1   0.529308   1.0   87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   
593        1   0.526546   2.0   95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   
597        1   0.533702  21.0   87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   

     X_10   X_11   X_12   X_13  X_14  X_15   X_16   X_17   X_18   X_19   X_20  \
22    2.0  514.4  522.1  505.8   0.0   0.0  247.5  248.0  247.2  250.0  481.0   
23    2.0  514.6  522.6  506.0   0.0   0.0  247.6  248.1  247.4  250.0  481.0   
25    2.0  517.4  526.0  508.9   0.0   0.0  247.5  247.8  247.3  250.0  478.0   
29    2.0  516.5  526.0  507.5   0.0   0.0  247.6  248.1  247.4  250.0  479.0   
37    2.0  517.5  526.7  508.4   0.0   0.0  247.5  248.1  247.2  250.0  478.0   
..    ...    ...    ...    ...   ...   ...    ...    ...    ...    ...    ...   
589   2.0  465.5  470.2  456.1   0.0   0.0  247.5  248.0  247.3  250.0  531.0   
590   2.0  466.0  470.5  458.0   0.0   0.0  247.5  248.0  247.3  250.0  530.0   
591   2.0  465.9  470.5  456.8   0.0   0.0  247.6  248.0  247.2  250.0  530.0   
593   2.0  468.9  473.9  459.2   0.0   0.0  247.5  248.0  247.3  250.0  527.0   
597   2.0  470.6  474.9  462.9   0.0   0.0  247.5  248.0  247.3  250.0  525.0   

      X_21   X_22  X_23  X_24  X_25   X_26   X_27   X_28   X_29   X_30   X_31  \
22   490.0  474.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
23   489.0  474.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
25   486.0  470.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
29   488.0  471.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
37   486.0  470.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
..     ...    ...   ...   ...   ...    ...    ...    ...    ...    ...    ...   
589  541.0  526.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
590  540.0  526.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
591  542.0  526.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
593  538.0  522.0  0.19  0.19  0.19  155.0  155.0  155.0  155.0  185.0  185.0   
597  534.0  520.0  0.19  0.20  0.19  155.0  155.0  155.0  155.0  185.0  185.0   

      X_32   X_33   X_34   X_35   X_36   X_37   X_38  X_39  X_40  X_41  X_42  \
22   185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.7  64.6  64.7   
23   185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.7  64.6  64.7   
25   185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.1  64.1  65.2   
29   185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.1  64.1  65.2   
37   185.0  185.0  155.0  155.0  155.0  155.0  0.079   2.0  63.1  64.1  65.2   
..     ...    ...    ...    ...    ...    ...    ...   ...   ...   ...   ...   
589  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0  67.2  68.9  67.5   
590  185.0  185.0  155.0  155.0  155.0  155.0  0.076   2.0  67.2  68.9  67.5   
591  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0  67.2  68.9  67.5   
593  185.0  185.0  155.0  155.0  155.0  155.0  0.075   2.0  67.2  68.9  67.5   
597  185.0  185.0  155.0  155.0  155.0  155.0  0.077   1.0  67.2  68.9  67.5   

     X_43  X_44  X_45  X_46  X_47  X_48  X_49  X_50  X_51  X_52  X_53  X_54  \
22   78.6  69.0  82.2  70.4  64.7  74.3  76.4  66.1  79.5 

In [249]:
T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

# T05

In [250]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)

In [144]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
1     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
2     -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
3     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
4     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
116   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
117   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
118   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
119   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

        X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
0   -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454    0.0   
1   -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040    0.0   
2   -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877    0.0   
3   -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990    0.0   
4   -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680    0.0   
..        ...       ...    ...    ...    ...    ...       ...    ...   
115 -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057    0.0   
116 -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895    0.0   
117 -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307    0.0   
118 -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895    0.0   
119 -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921    0.0   

        X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
0    0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   
1   -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0   
2    0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0    0.1   
3    0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0    0.0   
4    0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0   
..        ...       ...     ...    ...    ...    ...    ...    ...    ...   
115  1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   
116  1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0   
117  1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0    0.0   
118  1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0    0.0   
119  1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0    0.0   

     X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
0      0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
1      0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
2      0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
3      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5    0.0   
4      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
115    0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
116    0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
117    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5    0.0   
118   -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5    0.0   
119    0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0.5    0.0   

     X_167  X_168  X_169  X_170  X_171  X_172  X_173  X_174  X_175  X_176  \
0     -1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
1     -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
2     -1.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0   
3      0.0    0.0    0.0    0.0   -1.0    0.0    0.0    0.0    1.0    0.0   
4   

In [145]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
index                                                                       
0       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
2       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
4       -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
6       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
8       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
...      ...    ...    ...    ...       ...       ...       ...       ...   
549     -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
550     -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
551     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
552     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
555     -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

          X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
index                                                                    
0     -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454    0.0   
2     -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040    0.0   
4     -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877    0.0   
6     -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990    0.0   
8     -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680    0.0   
...         ...       ...    ...    ...    ...    ...       ...    ...   
549   -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057    0.0   
550   -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895    0.0   
551   -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307    0.0   
552   -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895    0.0   
555   -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921    0.0   

          X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
index                                                                         
0      0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   
2     -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0   
4      0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0    0.1   
6      0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0    0.0   
8      0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...       ...     ...    ...    ...    ...    ...    ...    ...   
549    1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   
550    1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0   
551    1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0    0.0   
552    1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0    0.0   
555    1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0    0.0   

       X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
index                                                                         
0        0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
2        0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
4        0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
6        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5    0.0   
8        0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
550      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
551      0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5    0.0   
552     -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5    0.0   
555      0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0

In [146]:
T05_data[T05_data.columns]

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
index                                                                       
0       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
2       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
4       -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
6       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
8       -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
...      ...    ...    ...    ...       ...       ...       ...       ...   
549     -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
550     -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
551     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
552     -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
555     -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

          X_140     X_141  X_142  X_143  X_144  X_145     X_146  X_147  \
index                                                                    
0     -0.052154  0.023438    0.0    0.0   -1.0    0.0 -0.003454    0.0   
2     -0.029478  0.315104    0.0    0.0    0.0    0.0  0.563040    0.0   
4     -0.043084 -0.049479    0.0    0.0   -1.0    0.0 -0.348877    0.0   
6     -0.043084 -1.195312    0.0    0.0   -2.0    0.0 -4.113990    0.0   
8     -0.047619  0.263021    0.0    0.0    0.0    0.0  0.514680    0.0   
...         ...       ...    ...    ...    ...    ...       ...    ...   
549   -0.882086 -0.898437    0.0    0.0    0.0    0.0  0.373057    0.0   
550   -0.891156 -0.929687    0.0    0.0   -1.0    0.0  0.158895    0.0   
551   -0.886621 -0.695312    0.0    0.0    0.0    0.0  0.618307    0.0   
552   -0.877551 -0.919271    0.0    0.0    0.0    0.0  0.158895    0.0   
555   -0.877551 -1.263021    0.0    0.0   -1.0    0.0 -0.873921    0.0   

          X_148     X_149   X_150  X_151  X_152  X_153  X_154  X_155  X_156  \
index                                                                         
0      0.000000  0.072727  0.0625   -1.0    0.0    0.0    0.0    0.0    0.0   
2     -0.074074  0.000000  0.0000   -1.0    0.0   -1.0    0.0    0.0    0.0   
4      0.000000  0.000000  0.0625    0.0    0.0   -1.0    0.0    0.0    0.1   
6      0.000000  0.000000  0.0000    0.0    0.1    0.0    0.0   -1.0    0.0   
8      0.000000  0.000000  0.0625    0.0    0.0    0.0    0.0    0.0    0.0   
...         ...       ...     ...    ...    ...    ...    ...    ...    ...   
549    1.037037  1.163636  0.8750   -1.0    0.0   -2.0    0.0    0.0    0.0   
550    1.037037  1.163636  0.8750    0.0    0.0    0.0    0.0    0.0    0.0   
551    1.037037  1.163636  0.8750   -1.0    0.0   -1.0    0.0   -1.0    0.0   
552    1.037037  1.163636  0.8750   -1.0   -0.1   -1.0    0.0    0.0    0.0   
555    1.111111  1.236364  0.8750    0.0    0.0    0.0    0.0   -1.0    0.0   

       X_157  X_158  X_159  X_160  X_161  X_162  X_163  X_164  X_165  X_166  \
index                                                                         
0        0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
2        0.0    0.0    0.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
4        0.1    0.0   -1.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
6        0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   -0.5    0.0   
8        0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
549      0.0    0.0   -1.0    0.0    0.0    0.0   -0.1    0.0   -0.5    0.0   
550      0.0    0.0    0.0    0.0    0.0    0.0    0.0    1.0    0.5    0.0   
551      0.0    0.0   -1.0    0.0    0.0    0.0    0.0    0.0    0.5    0.0   
552     -0.1    0.0   -1.0    0.1    0.0    0.0   -0.1    0.0   -0.5    0.0   
555      0.0    0.0    0.0    0.1    0.0    0.0    0.0    0.0    0

In [147]:
T05_data = T05_data.to_numpy()
#T05_target = np.log1p(T05_target)
T05_target = T05_target.to_numpy().reshape(-1, 1)

In [148]:
kf = KFold(n_splits=5, random_state=414, shuffle=True)
predictions_array =[]
CV_score_array    =[]
for train_index, test_index in kf.split(T05_data):
    T05_data_train, T05_data_valid = T05_data[train_index], T05_data[test_index]
    T05_target_train, T05_target_valid = T05_target[train_index], T05_target[test_index]
    T05_regressor = TabNetRegressor(verbose=0, seed=42)
    T05_regressor.fit(X_train=T05_data_train, y_train=T05_target_train,
              eval_set=[(T05_data_valid, T05_target_valid)],
              patience=300, max_epochs=2000,
              eval_metric=['rmse'])
    CV_score_array.append(T05_regressor.best_cost)
    #predictions_array.append(np.expm1(regressor.predict(X_test)))

    print("The CV score is %.5f" % np.mean(CV_score_array,axis=0) )    
#predictions = np.mean(predictions_array,axis=0)


Early stopping occurred at epoch 609 with best_epoch = 309 and best_val_0_rmse = 0.02493
Best weights from best epoch are automatically used!
The CV score is 0.02493

Early stopping occurred at epoch 622 with best_epoch = 322 and best_val_0_rmse = 0.03456
Best weights from best epoch are automatically used!
The CV score is 0.02975

Early stopping occurred at epoch 573 with best_epoch = 273 and best_val_0_rmse = 0.04478
Best weights from best epoch are automatically used!
The CV score is 0.03476

Early stopping occurred at epoch 482 with best_epoch = 182 and best_val_0_rmse = 0.03199
Best weights from best epoch are automatically used!
The CV score is 0.03407

Early stopping occurred at epoch 518 with best_epoch = 218 and best_val_0_rmse = 0.02391
Best weights from best epoch are automatically used!
The CV score is 0.03204


In [155]:
T05_datas = T05_regressor.predict(T05_data)
T05_datas = pd.DataFrame(T05_datas, columns = ['Y_Quality'])
T05_datas

Y_Quality
0     0.507932
1     0.544106
2     0.526415
3     0.518035
4     0.522243
..         ...
115   0.536195
116   0.533497
117   0.536989
118   0.533728
119   0.532827

[120 rows x 1 columns]

In [156]:
T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.507932
2       0.544106
4       0.526415
6       0.518035
8       0.522243
...          ...
549     0.536195
550     0.533497
551     0.536989
552     0.533728
555     0.532827

[120 rows x 1 columns]

In [157]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [158]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [159]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [160]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                        criterion='entropy', max_depth=5, max_features='sqrt',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.3, min_samples_leaf=3,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=170, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_

In [161]:
for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.4969
85    0.531607        0                 1            0.4923
86    0.490927        1                 0            0.4969
87    0.512871        0                 0            0.5260
88    0.489542        2                 0            0.4969
89    0.522207        0                 0            0.4583
90    0.522959        1                 0            0.4583
91    0.584384        2                 2            0.6835
92    0.535007        1                 1            0.5638
93    0.544910        1                 2            0.6835
94    0.524705        0                 1            0.5923
95    0.512766        2                 0            0.5260
96    0.522243        1                 0            0.4583
97    0.506005        1                 0            0.4969
98    0.531520        2                 1            0.4923
99    0.499847        1                 0            0.4969
100   0.504610        1                 0            0.4969
101   0.554046        2                 2            0.6835
102   0.515535        2                 0            0.4427
103   0.501981        0                 0            0.4969
104   0.518737        1                 1            0.4619
105   0.591706        0                 2            0.6835
106   0.528170        2                 1            0.4774
107   0.518035        1                 1            0.4619
108   0.529803        0                 1            0.4774
109   0.550884        2                 2            0.6835
110   0.519724        2                 0            0.4583
111   0.542556        0                 2            0.6835
112   0.517443        0                 0            0.4427
113   0.524286        0                 1            0.5923
114   0.498219        0                 0            0.4969
115   0.544106        1                 2            0.6835
116   0.518006        1                 1            0.4619
117   0.541675        1                 2            0.6835
118   0.584931        1                 2            0.6835
119   0.538172        2                 1            0.4835

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 1            0.3907
85    0.531607        0                 1            0.3907
86    0.490927        1                 1            0.3907
87    0.512871        0                 1            0.3907
88    0.489542        2                 1            0.3907
89    0.522207        0                 1            0.3907
90    0.522959        1                 1            0.3907
91    0.584384        2                 1            0.3760
92    0.535007        1                 1            0.3914
93    0.544910        1                 1            0.3760
94    0.524705        0                 1            0.3907
95    0.512766        2                 1            0.3907
96    0.522243        1                 1            0.3907
97    0.506005        1                 1            0.3907
98    0.531520        2                 1            0.3907
99    0.499847        1                 1            0.3907
100   0.504610        1                 1            0.3907
101   0.554046        2                 1            0.3760
102   0.515535        2                 1            0.3907
103   0.501981        0                 1            0.3907
104   0.518737        1                 1            0.3907
105   0.591706        0                 1            0.3760
106   0.528170        2                 1            0.3907
107   0.518035        1                 1            0.3907
108   0.529803        0                 1            0.3907
109   0.550884        2                 1            0.3760
110   0.519724        2                 1            0.3907
111   0.542556        0                 1            0.3760
112   0.517443        0                 1            0.3907
113   0.524286        0                 1            0.3907
114   0.498219        0                 1            0.3907
115   0.544106        1                 1            0.3760
116   0.518006        1                 1            0.3907
117   0.541675        1                 1            0.3760
118   0.584931        1                 1            0.3760
119   0.538172        2                 1            0.3883

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.6529
85    0.531607        0                 0            0.4934
86    0.490927        1                 0            0.5935
87    0.512871        0                 0            0.5974
88    0.489542        2                 0            0.6176
89    0.522207        0                 0            0.5839
90    0.522959        1                 1            0.5942
91    0.584384        2                 0            0.7612
92    0.535007        1                 1            0.8484
93    0.544910        1                 2            0.9058
94    0.524705        0                 1            0.6032
95    0.512766        2                 0            0.4845
96    0.522243        1                 0            0.5839
97    0.506005        1                 1            0.4860
98    0.531520        2                 0            0.4934
99    0.499847        1                 0            0.5935
100   0.504610        1                 0            0.4581
101   0.554046        2                 2            0.5292
102   0.515535        2                 1            0.5323
103   0.501981        0                 0            0.7371
104   0.518737        1                 1            0.4236
105   0.591706        0                 0            0.7612
106   0.528170        2                 0            0.4958
107   0.518035        1                 1            0.5082
108   0.529803        0                 0            0.5114
109   0.550884        2                 2            0.7094
110   0.519724        2                 0            0.4321
111   0.542556        0                 2            0.8370
112   0.517443        0                 0            0.5091
113   0.524286        0                 1            0.4526
114   0.498219        0                 0            0.5935
115   0.544106        1                 2            0.8858
116   0.518006        1                 1            0.5082
117   0.541675        1                 2            0.8296
118   0.584931        1                 0            0.7612
119   0.538172        2                 1            0.4595

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.3631
85    0.531607        0                 1            0.3612
86    0.490927        1                 0            0.3631
87    0.512871        0                 0            0.3559
88    0.489542        2                 0            0.3631
89    0.522207        0                 1            0.3521
90    0.522959        1                 1            0.3521
91    0.584384        2                 2            0.3784
92    0.535007        1                 1            0.3568
93    0.544910        1                 2            0.3759
94    0.524705        0                 1            0.3554
95    0.512766        2                 0            0.3564
96    0.522243        1                 1            0.3521
97    0.506005        1                 0            0.3631
98    0.531520        2                 1            0.3612
99    0.499847        1                 0            0.3631
100   0.504610        1                 0            0.3631
101   0.554046        2                 2            0.3784
102   0.515535        2                 0            0.3531
103   0.501981        0                 0            0.3631
104   0.518737        1                 0            0.3482
105   0.591706        0                 2            0.3784
106   0.528170        2                 1            0.3591
107   0.518035        1                 0            0.3480
108   0.529803        0                 1            0.3586
109   0.550884        2                 2            0.3784
110   0.519724        2                 1            0.3475
111   0.542556        0                 2            0.3734
112   0.517443        0                 0            0.3480
113   0.524286        0                 1            0.3554
114   0.498219        0                 0            0.3631
115   0.544106        1                 2            0.3759
116   0.518006        1                 0            0.3480
117   0.541675        1                 2            0.3734
118   0.584931        1                 2            0.3784
119   0.538172        2                 1            0.3460

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.3499
85    0.531607        0                 1            0.3505
86    0.490927        1                 0            0.3494
87    0.512871        0                 0            0.3442
88    0.489542        2                 0            0.3494
89    0.522207        0                 1            0.3448
90    0.522959        1                 1            0.3466
91    0.584384        2                 2            0.3567
92    0.535007        1                 1            0.3540
93    0.544910        1                 2            0.3651
94    0.524705        0                 1            0.3496
95    0.512766        2                 0            0.3443
96    0.522243        1                 1            0.3448
97    0.506005        1                 0            0.3454
98    0.531520        2                 1            0.3505
99    0.499847        1                 0            0.3494
100   0.504610        1                 0            0.3460
101   0.554046        2                 2            0.3610
102   0.515535        2                 0            0.3431
103   0.501981        0                 0            0.3495
104   0.518737        1                 1            0.3430
105   0.591706        0                 2            0.3567
106   0.528170        2                 1            0.3501
107   0.518035        1                 1            0.3426
108   0.529803        0                 1            0.3502
109   0.550884        2                 2            0.3610
110   0.519724        2                 1            0.3432
111   0.542556        0                 2            0.3651
112   0.517443        0                 0            0.3428
113   0.524286        0                 1            0.3496
114   0.498219        0                 0            0.3494
115   0.544106        1                 2            0.3651
116   0.518006        1                 1            0.3426
117   0.541675        1                 2            0.3646
118   0.584931        1                 2            0.3567
119   0.538172        2                 1            0.3460

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.3335
85    0.531607        0                 1            0.3335
86    0.490927        1                 0            0.3335
87    0.512871        0                 0            0.3335
88    0.489542        2                 0            0.3335
89    0.522207        0                 1            0.3335
90    0.522959        1                 1            0.3335
91    0.584384        2                 2            0.3336
92    0.535007        1                 1            0.3336
93    0.544910        1                 2            0.3336
94    0.524705        0                 1            0.3335
95    0.512766        2                 0            0.3335
96    0.522243        1                 1            0.3335
97    0.506005        1                 0            0.3335
98    0.531520        2                 1            0.3335
99    0.499847        1                 0            0.3335
100   0.504610        1                 0            0.3335
101   0.554046        2                 2            0.3336
102   0.515535        2                 0            0.3335
103   0.501981        0                 0            0.3335
104   0.518737        1                 1            0.3335
105   0.591706        0                 2            0.3336
106   0.528170        2                 1            0.3335
107   0.518035        1                 1            0.3335
108   0.529803        0                 1            0.3335
109   0.550884        2                 2            0.3336
110   0.519724        2                 1            0.3335
111   0.542556        0                 2            0.3336
112   0.517443        0                 1            0.3335
113   0.524286        0                 1            0.3335
114   0.498219        0                 0            0.3335
115   0.544106        1                 2            0.3336
116   0.518006        1                 1            0.3335
117   0.541675        1                 2            0.3336
118   0.584931        1                 2            0.3336
119   0.538172        2                 1            0.3334

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.486424        0                 0            0.3809
85    0.531607        0                 1            0.3595
86    0.490927        1                 0            0.3809
87    0.512871        0                 0            0.3423
88    0.489542        2                 0            0.3809
89    0.522207        0                 0            0.3423
90    0.522959        1                 1            0.3413
91    0.584384        2                 0            0.3926
92    0.535007        1                 1            0.3620
93    0.544910        1                 2            0.3881
94    0.524705        0                 1            0.3419
95    0.512766        2                 0            0.3423
96    0.522243        1                 0            0.3423
97    0.506005        1                 1            0.3448
98    0.531520        2                 1            0.3595
99    0.499847        1                 0            0.3809
100   0.504610        1                 1            0.3467
101   0.554046        2                 2            0.3881
102   0.515535        2                 0            0.3423
103   0.501981        0                 0            0.3809
104   0.518737        1                 0            0.3423
105   0.591706        0                 0            0.3926
106   0.528170        2                 1            0.3595
107   0.518035        1                 0            0.3423
108   0.529803        0                 1            0.3595
109   0.550884        2                 2            0.3881
110   0.519724        2                 0            0.3423
111   0.542556        0                 2            0.3881
112   0.517443        0                 0            0.3423
113   0.524286        0                 1            0.3419
114   0.498219        0                 0            0.3809
115   0.544106        1                 2            0.3881
116   0.518006        1                 0            0.3423
117   0.541675        1                 2            0.3881
118   0.584931        1                 0            0.3926
119   0.538172        2                 1            0.3620

In [162]:
T05_vote_classification_models = [
    ('ada',  T05_model_ada),
    ('lightgbm', T05_model_lightgbm),
    ('rf', T05_model_rf),
    ('gbc', T05_model_gbc),
    ('et', T05_model_et),
    ('cat', T05_model_catboost),
    ('xgb', T05_model_xgb),
]

In [163]:
T05_soft_vote = VotingClassifier(T05_vote_classification_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T05_soft_vote.fit(T05_datas, T05_class)

VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME.R',
                                                 base_estimator=None,
                                                 learning_rate=0.05,
                                                 n_estimators=290,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             importance_type='split',
                                             learning_rate=0.1, max_depth=-1,
                                             min_child_samples=20,
                                             min_child_weight=0.001,
                                             min_split_gain...
                               

In [164]:
T05_prediction = pd.DataFrame(T05_soft_vote.predict(T05_datas), columns = ['prediction_label'])
T05_prediction

prediction_label
0                   1
1                   1
2                   1
3                   1
4                   1
..                ...
115                 1
116                 1
117                 1
118                 1
119                 0

[120 rows x 1 columns]

In [ ]:
T05_final_classification_model = finalize_model(T05_model_lightgbm)

In [ ]:
T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)
T05_prediction

In [165]:
T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [168]:
T05_prediction

prediction_label
index                  
0                     1
2                     1
4                     1
6                     1
8                     1
...                 ...
549                   1
550                   1
551                   1
552                   1
555                   0

[120 rows x 1 columns]

# T01

In [251]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)
T01_data

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  \
28     1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   42.0    2.0   
33     1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   42.0    2.0   
39     1.0   95.0    0.0   45.0   11.0  102.0   45.0   12.0   42.0    2.0   
40     1.0   95.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
41     1.0   87.0    0.0   45.0   11.0  105.0   45.0   11.0   42.0    2.0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
479    1.0   93.0  107.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
501    2.0   95.0  124.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
523    1.0   89.0  136.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
531    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
585    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   

     ...      X_2858  X_2859  X_2860      X_2861  X_2862  X_2863      X_2864  \
28   ...  182.758621   175.7   182.0  174.727586   160.5   446.0  429.716981   
33   ...  184.365517   171.4   175.7  168.258621   158.3   446.0  429.301887   
39   ...  173.068965   163.7   184.1  173.479310   165.8   447.0  427.867925   
40   ...  180.396429   152.7   191.8  178.832143   168.6   446.0  428.403846   
41   ...  172.751724   146.9   182.4  170.379310   162.9   446.0  429.094340   
..   ...         ...     ...     ...         ...     ...     ...         ...   
479  ...  193.278571   177.5   183.3  169.553571   154.2   456.0  438.132075   
501  ...  197.392857   173.1   187.6  182.142857   175.1   466.0  445.307692   
523  ...  194.860714   183.9   189.2  181.700000   172.7   466.0  444.615385   
531  ...  190.407143   181.1   192.6  185.207143   173.2   466.0  446.038461   
585  ...  205.079310   196.1   192.2  187.396552   176.7   472.0  450.339623   

     X_2865  HOUR  DAY_OF_WEEK  
28    413.0    20            7  
33    413.0     7            2  
39    407.0     4            3  
40    413.0    12            3  
41    406.0    12            3  
..      ...   ...          ...  
479   413.0    15            2  
501   425.0    15            5  
523   423.0    10            7  
531   427.0    15            1  
585   432.0    11            1  

[129 rows x 880 columns]

In [170]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
1      0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
2      0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
3      0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
4      0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
..     ...    ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
125    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
128    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
0      0.0  ... -0.390876  0.000000 -0.053030  0.321839  0.041096    -1.9   
1      0.0  ... -0.287500 -0.222798 -0.530303 -0.217241 -0.109589    -1.9   
2      0.0  ... -1.014237 -0.621762  0.106061  0.217816  0.404110    -1.8   
3      0.0  ... -0.542842 -1.191710  0.689394  0.663885  0.595890    -1.9   
4      0.0  ... -1.034646 -1.492228 -0.022727 -0.040517  0.205479    -1.9   
..     ...  ...       ...       ...       ...       ...       ...     ...   
124    0.0  ...  0.285900  0.093264  0.045455 -0.109329 -0.390411    -0.9   
125    0.0  ...  0.550583 -0.134715  0.371212  0.939778  1.041096     0.1   
126    0.0  ...  0.387683  0.424870  0.492424  0.902874  0.876712     0.1   
127    0.0  ...  0.101173  0.279793  0.750000  1.195135  0.910959     0.1   
128    0.0  ...  1.045072  1.056995  0.719697  1.377586  1.150685     0.7   

       X_2864  X_2865      HOUR  DAY_OF_WEEK  
0   -1.452964    -5.0  0.777778     0.666667  
1   -1.500816    -5.0 -0.666667    -1.000000  
2   -1.666123    -8.0 -1.000000    -0.666667  
3   -1.604342    -5.0 -0.111111    -0.666667  
4   -1.524742    -8.5 -0.111111    -0.666667  
..        ...     ...       ...          ...  
124 -0.482871    -5.0  0.222222    -1.000000  
125  0.344334     1.0  0.222222     0.000000  
126  0.264525     0.0 -0.333333     0.666667  
127  0.428577     2.0  0.222222    -1.333333  
128  0.924415     4.5 -0.222222    -1.333333  

[129 rows x 880 columns]

In [171]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
index                                                                        
28       0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
33       0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
39       0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
40       0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
41       0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
...      ...    ...       ...    ...    ...       ...    ...    ...    ...   
479      0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
501      1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
523      0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
531      0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
585      0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

       X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
index         ...                                                             
28       0.0  ... -0.390876  0.000000 -0.053030  0.321839  0.041096    -1.9   
33       0.0  ... -0.287500 -0.222798 -0.530303 -0.217241 -0.109589    -1.9   
39       0.0  ... -1.014237 -0.621762  0.106061  0.217816  0.404110    -1.8   
40       0.0  ... -0.542842 -1.191710  0.689394  0.663885  0.595890    -1.9   
41       0.0  ... -1.034646 -1.492228 -0.022727 -0.040517  0.205479    -1.9   
...      ...  ...       ...       ...       ...       ...       ...     ...   
479      0.0  ...  0.285900  0.093264  0.045455 -0.109329 -0.390411    -0.9   
501      0.0  ...  0.550583 -0.134715  0.371212  0.939778  1.041096     0.1   
523      0.0  ...  0.387683  0.424870  0.492424  0.902874  0.876712     0.1   
531      0.0  ...  0.101173  0.279793  0.750000  1.195135  0.910959     0.1   
585      0.0  ...  1.045072  1.056995  0.719697  1.377586  1.150685     0.7   

         X_2864  X_2865      HOUR  DAY_OF_WEEK  
index                                           
28    -1.452964    -5.0  0.777778     0.666667  
33    -1.500816    -5.0 -0.666667    -1.000000  
39    -1.666123    -8.0 -1.000000    -0.666667  
40    -1.604342    -5.0 -0.111111    -0.666667  
41    -1.524742    -8.5 -0.111111    -0.666667  
...         ...     ...       ...          ...  
479   -0.482871    -5.0  0.222222    -1.000000  
501    0.344334     1.0  0.222222     0.000000  
523    0.264525     0.0 -0.333333     0.666667  
531    0.428577     2.0  0.222222    -1.333333  
585    0.924415     4.5 -0.222222    -1.333333  

[129 rows x 880 columns]

In [172]:
T01_data = T01_data.to_numpy()
#T05_target = np.log1p(T05_target)
T01_target = T01_target.to_numpy().reshape(-1, 1)

In [173]:
kf = KFold(n_splits=5, random_state=414, shuffle=True)
predictions_array =[]
CV_score_array    =[]
for train_index, test_index in kf.split(T01_data):
    T01_data_train, T01_data_valid = T01_data[train_index], T01_data[test_index]
    T01_target_train, T01_target_valid = T01_target[train_index], T01_target[test_index]
    T01_regressor = TabNetRegressor(verbose=0, seed=42)
    T01_regressor.fit(X_train=T01_data_train, y_train=T01_target_train,
              eval_set=[(T01_data_valid, T01_target_valid)],
              patience=300, max_epochs=2000,
              eval_metric=['rmse'])
    CV_score_array.append(T01_regressor.best_cost)
    #predictions_array.append(np.expm1(regressor.predict(X_test)))

    print("The CV score is %.5f" % np.mean(CV_score_array,axis=0) )    
#predictions = np.mean(predictions_array,axis=0)


Early stopping occurred at epoch 513 with best_epoch = 213 and best_val_0_rmse = 0.0542
Best weights from best epoch are automatically used!
The CV score is 0.05420

Early stopping occurred at epoch 429 with best_epoch = 129 and best_val_0_rmse = 0.04744
Best weights from best epoch are automatically used!
The CV score is 0.05082

Early stopping occurred at epoch 434 with best_epoch = 134 and best_val_0_rmse = 0.08926
Best weights from best epoch are automatically used!
The CV score is 0.06363

Early stopping occurred at epoch 461 with best_epoch = 161 and best_val_0_rmse = 0.03373
Best weights from best epoch are automatically used!
The CV score is 0.05616

Early stopping occurred at epoch 505 with best_epoch = 205 and best_val_0_rmse = 0.05513
Best weights from best epoch are automatically used!
The CV score is 0.05595


In [174]:
T01_datas = T01_regressor.predict(T01_data)
T01_datas = pd.DataFrame(T01_datas, columns = ['Y_Quality'])
T01_datas

Y_Quality
0     0.508487
1     0.576952
2     0.466590
3     0.489936
4     0.613787
..         ...
124   0.514600
125   0.527809
126   0.507573
127   0.559210
128   0.541921

[129 rows x 1 columns]

In [175]:
T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
28      0.508487
33      0.576952
39      0.466590
40      0.489936
41      0.613787
...          ...
479     0.514600
501     0.527809
523     0.507573
531     0.559210
585     0.541921

[129 rows x 1 columns]

In [176]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [177]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [178]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [179]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMClassifier(bagging_fraction=0.8, bagging_freq=2, boosting_type='gbdt',
                class_weight=None, colsample_bytree=1.0, feature_fraction=0.7,
                importance_type='split', learning_rate=0.005, max_depth=-1,
                min_child_samples=1, min_child_weight=0.001, min_split_gain=0.6,
                n_estimators=30, n_jobs=-1, num_leaves=40, objective=None,
                random_state=414, reg_alpha=0.1, reg_lambda=10, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                        criterion='entropy', max_depth=5, max_features='sqrt',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.3, min_samples_leaf=3,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=170, n_jobs=-1, oob_score=False,
                        rando

In [180]:
for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.5500
91    0.516587        0                 1            0.5424
92    0.475669        0                 1            0.5426
93    0.527853        0                 1            0.5461
94    0.502224        1                 1            0.5424
95    0.523176        0                 1            0.5461
96    0.537707        1                 1            0.5500
97    0.559210        2                 1            0.5588
98    0.523758        2                 1            0.5461
99    0.498492        2                 1            0.5424
100   0.492234        1                 1            0.5426
101   0.446562        2                 1            0.5426
102   0.515138        2                 1            0.5424
103   0.497619        1                 1            0.5424
104   0.581945        2                 1            0.5588
105   0.456502        1                 1            0.5426
106   0.505338        1                 1            0.5424
107   0.554549        1                 1            0.5588
108   0.477849        1                 1            0.5426
109   0.525844        0                 1            0.5461
110   0.613787        1                 1            0.5588
111   0.592389        2                 1            0.5588
112   0.529708        1                 1            0.5461
113   0.467772        1                 1            0.5426
114   0.498360        2                 1            0.5424
115   0.500208        2                 1            0.5424
116   0.501240        1                 1            0.5424
117   0.505795        1                 1            0.5424
118   0.549306        1                 1            0.5588
119   0.502912        1                 1            0.5424
120   0.557041        1                 1            0.5588
121   0.458117        1                 1            0.5426
122   0.466590        1                 1            0.5426
123   0.519235        1                 1            0.5447
124   0.500596        1                 1            0.5424
125   0.474509        1                 1            0.5426
126   0.542023        2                 1            0.5500
127   0.523223        0                 1            0.5461
128   0.528122        2                 1            0.5461

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.5571
91    0.516587        0                 1            0.5571
92    0.475669        0                 1            0.5571
93    0.527853        0                 1            0.5571
94    0.502224        1                 1            0.5571
95    0.523176        0                 1            0.5571
96    0.537707        1                 1            0.5571
97    0.559210        2                 1            0.5571
98    0.523758        2                 1            0.5571
99    0.498492        2                 1            0.5571
100   0.492234        1                 1            0.5571
101   0.446562        2                 1            0.5571
102   0.515138        2                 1            0.5571
103   0.497619        1                 1            0.5571
104   0.581945        2                 1            0.5571
105   0.456502        1                 1            0.5571
106   0.505338        1                 1            0.5571
107   0.554549        1                 1            0.5571
108   0.477849        1                 1            0.5571
109   0.525844        0                 1            0.5571
110   0.613787        1                 1            0.5571
111   0.592389        2                 1            0.5571
112   0.529708        1                 1            0.5571
113   0.467772        1                 1            0.5571
114   0.498360        2                 1            0.5571
115   0.500208        2                 1            0.5571
116   0.501240        1                 1            0.5571
117   0.505795        1                 1            0.5571
118   0.549306        1                 1            0.5571
119   0.502912        1                 1            0.5571
120   0.557041        1                 1            0.5571
121   0.458117        1                 1            0.5571
122   0.466590        1                 1            0.5571
123   0.519235        1                 1            0.5571
124   0.500596        1                 1            0.5571
125   0.474509        1                 1            0.5571
126   0.542023        2                 1            0.5571
127   0.523223        0                 1            0.5571
128   0.528122        2                 1            0.5571

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.5563
91    0.516587        0                 1            0.5542
92    0.475669        0                 1            0.5528
93    0.527853        0                 1            0.5556
94    0.502224        1                 1            0.5540
95    0.523176        0                 1            0.5548
96    0.537707        1                 1            0.5565
97    0.559210        2                 1            0.5594
98    0.523758        2                 1            0.5554
99    0.498492        2                 1            0.5546
100   0.492234        1                 1            0.5548
101   0.446562        2                 1            0.5528
102   0.515138        2                 1            0.5541
103   0.497619        1                 1            0.5546
104   0.581945        2                 1            0.5594
105   0.456502        1                 1            0.5528
106   0.505338        1                 1            0.5539
107   0.554549        1                 1            0.5593
108   0.477849        1                 1            0.5528
109   0.525844        0                 1            0.5556
110   0.613787        1                 1            0.5594
111   0.592389        2                 1            0.5594
112   0.529708        1                 1            0.5555
113   0.467772        1                 1            0.5528
114   0.498360        2                 1            0.5546
115   0.500208        2                 1            0.5546
116   0.501240        1                 1            0.5542
117   0.505795        1                 1            0.5539
118   0.549306        1                 1            0.5586
119   0.502912        1                 1            0.5540
120   0.557041        1                 1            0.5593
121   0.458117        1                 1            0.5528
122   0.466590        1                 1            0.5528
123   0.519235        1                 1            0.5546
124   0.500596        1                 1            0.5542
125   0.474509        1                 1            0.5528
126   0.542023        2                 1            0.5564
127   0.523223        0                 1            0.5548
128   0.528122        2                 1            0.5556

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.5571
91    0.516587        0                 1            0.5571
92    0.475669        0                 1            0.5571
93    0.527853        0                 1            0.5571
94    0.502224        1                 1            0.5571
95    0.523176        0                 1            0.5571
96    0.537707        1                 1            0.5571
97    0.559210        2                 1            0.5571
98    0.523758        2                 1            0.5571
99    0.498492        2                 1            0.5571
100   0.492234        1                 1            0.5571
101   0.446562        2                 1            0.5571
102   0.515138        2                 1            0.5571
103   0.497619        1                 1            0.5571
104   0.581945        2                 1            0.5571
105   0.456502        1                 1            0.5571
106   0.505338        1                 1            0.5571
107   0.554549        1                 1            0.5571
108   0.477849        1                 1            0.5571
109   0.525844        0                 1            0.5571
110   0.613787        1                 1            0.5571
111   0.592389        2                 1            0.5571
112   0.529708        1                 1            0.5571
113   0.467772        1                 1            0.5571
114   0.498360        2                 1            0.5571
115   0.500208        2                 1            0.5571
116   0.501240        1                 1            0.5571
117   0.505795        1                 1            0.5571
118   0.549306        1                 1            0.5571
119   0.502912        1                 1            0.5571
120   0.557041        1                 1            0.5571
121   0.458117        1                 1            0.5571
122   0.466590        1                 1            0.5571
123   0.519235        1                 1            0.5571
124   0.500596        1                 1            0.5571
125   0.474509        1                 1            0.5571
126   0.542023        2                 1            0.5571
127   0.523223        0                 1            0.5571
128   0.528122        2                 1            0.5571

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.3352
91    0.516587        0                 1            0.3347
92    0.475669        0                 1            0.3348
93    0.527853        0                 1            0.3352
94    0.502224        1                 1            0.3348
95    0.523176        0                 1            0.3350
96    0.537707        1                 1            0.3352
97    0.559210        2                 1            0.3355
98    0.523758        2                 1            0.3351
99    0.498492        2                 1            0.3350
100   0.492234        1                 1            0.3351
101   0.446562        2                 1            0.3347
102   0.515138        2                 1            0.3347
103   0.497619        1                 1            0.3350
104   0.581945        2                 1            0.3354
105   0.456502        1                 1            0.3347
106   0.505338        1                 1            0.3347
107   0.554549        1                 1            0.3355
108   0.477849        1                 1            0.3348
109   0.525844        0                 1            0.3352
110   0.613787        1                 1            0.3354
111   0.592389        2                 1            0.3354
112   0.529708        1                 1            0.3351
113   0.467772        1                 1            0.3348
114   0.498360        2                 1            0.3350
115   0.500208        2                 1            0.3350
116   0.501240        1                 1            0.3349
117   0.505795        1                 1            0.3347
118   0.549306        1                 1            0.3354
119   0.502912        1                 1            0.3348
120   0.557041        1                 1            0.3355
121   0.458117        1                 1            0.3348
122   0.466590        1                 1            0.3348
123   0.519235        1                 1            0.3349
124   0.500596        1                 1            0.3349
125   0.474509        1                 1            0.3348
126   0.542023        2                 1            0.3352
127   0.523223        0                 1            0.3350
128   0.528122        2                 1            0.3352

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.3337
91    0.516587        0                 1            0.3335
92    0.475669        0                 1            0.3335
93    0.527853        0                 1            0.3336
94    0.502224        1                 1            0.3335
95    0.523176        0                 1            0.3336
96    0.537707        1                 1            0.3337
97    0.559210        2                 1            0.3337
98    0.523758        2                 1            0.3336
99    0.498492        2                 1            0.3335
100   0.492234        1                 1            0.3335
101   0.446562        2                 1            0.3335
102   0.515138        2                 1            0.3335
103   0.497619        1                 1            0.3335
104   0.581945        2                 1            0.3337
105   0.456502        1                 1            0.3335
106   0.505338        1                 1            0.3335
107   0.554549        1                 1            0.3337
108   0.477849        1                 1            0.3335
109   0.525844        0                 1            0.3336
110   0.613787        1                 1            0.3337
111   0.592389        2                 1            0.3337
112   0.529708        1                 1            0.3336
113   0.467772        1                 1            0.3335
114   0.498360        2                 1            0.3335
115   0.500208        2                 1            0.3335
116   0.501240        1                 1            0.3335
117   0.505795        1                 1            0.3335
118   0.549306        1                 1            0.3337
119   0.502912        1                 1            0.3335
120   0.557041        1                 1            0.3337
121   0.458117        1                 1            0.3335
122   0.466590        1                 1            0.3335
123   0.519235        1                 1            0.3336
124   0.500596        1                 1            0.3335
125   0.474509        1                 1            0.3335
126   0.542023        2                 1            0.3337
127   0.523223        0                 1            0.3336
128   0.528122        2                 1            0.3336

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.539916        1                 1            0.4519
91    0.516587        0                 1            0.4519
92    0.475669        0                 1            0.4519
93    0.527853        0                 1            0.4519
94    0.502224        1                 1            0.4519
95    0.523176        0                 1            0.4519
96    0.537707        1                 1            0.4519
97    0.559210        2                 1            0.4519
98    0.523758        2                 1            0.4519
99    0.498492        2                 1            0.4519
100   0.492234        1                 1            0.4519
101   0.446562        2                 1            0.4519
102   0.515138        2                 1            0.4519
103   0.497619        1                 1            0.4519
104   0.581945        2                 1            0.4519
105   0.456502        1                 1            0.4519
106   0.505338        1                 1            0.4519
107   0.554549        1                 1            0.4519
108   0.477849        1                 1            0.4519
109   0.525844        0                 1            0.4519
110   0.613787        1                 1            0.4519
111   0.592389        2                 1            0.4519
112   0.529708        1                 1            0.4519
113   0.467772        1                 1            0.4519
114   0.498360        2                 1            0.4519
115   0.500208        2                 1            0.4519
116   0.501240        1                 1            0.4519
117   0.505795        1                 1            0.4519
118   0.549306        1                 1            0.4519
119   0.502912        1                 1            0.4519
120   0.557041        1                 1            0.4519
121   0.458117        1                 1            0.4519
122   0.466590        1                 1            0.4519
123   0.519235        1                 1            0.4519
124   0.500596        1                 1            0.4519
125   0.474509        1                 1            0.4519
126   0.542023        2                 1            0.4519
127   0.523223        0                 1            0.4519
128   0.528122        2                 1            0.4519

In [181]:
T01_classifier_models = [
    ('ada',  T01_model_ada),
    ('lightgbm', T01_model_lightgbm),
    ('rf', T01_model_rf),
    ('gbc', T01_model_gbc),
    ('et', T01_model_et),
    ('cat', T01_model_catboost),
    ('xgb', T01_model_xgb),
]

In [182]:
T01_soft_vote = VotingClassifier(T01_classifier_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T01_soft_vote.fit(T01_datas, T01_class)

[LightGBM] [Warning] feature_fraction is set=0.7, colsample_bytree=1.0 will be ignored. Current value: feature_fraction=0.7
[LightGBM] [Warning] bagging_fraction is set=0.8, subsample=1.0 will be ignored. Current value: bagging_fraction=0.8
[LightGBM] [Warning] bagging_freq is set=2, subsample_freq=0 will be ignored. Current value: bagging_freq=2


VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME',
                                                 base_estimator=None,
                                                 learning_rate=0.001,
                                                 n_estimators=120,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(bagging_fraction=0.8,
                                             bagging_freq=2,
                                             boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             feature_fraction=0.7,
                                             importance_type='split',
                                             learning_rate=0.005, max_depth=-1,...
                               

In [183]:
T01_prediction = pd.DataFrame(T01_soft_vote.predict(T01_datas), columns = ['prediction_label'])
T01_prediction

prediction_label
0                   1
1                   1
2                   1
3                   1
4                   1
..                ...
124                 1
125                 1
126                 1
127                 1
128                 1

[129 rows x 1 columns]

In [184]:
T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

# T10

In [252]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)
T10_data

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  \
22    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
23    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
25    2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
29    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
37    2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
..    ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...   
589   1.0   94.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
590   1.0   89.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
591   1.0   87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
593   2.0   95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
597  21.0   87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0   2.0  ...   

          X_926  X_927  X_928       X_929  X_930  X_931      X_932  X_933  \
22   157.235484  150.9  326.0  309.290909  290.0   13.7  13.443333   13.2   
23     0.000000    0.0    0.0    0.000000    0.0    0.0   0.000000    0.0   
25   154.074194  150.9  327.0  310.854546  298.0   13.7  13.454839   13.2   
29   156.038710  149.1  327.0  312.109091  298.0   13.7  13.422581   13.2   
37   155.829032  148.4  327.0  312.254546  298.0   13.7  13.456667   13.3   
..          ...    ...    ...         ...    ...    ...        ...    ...   
589  154.309677  149.1  326.0  311.272727  298.0   13.7  13.483871   13.3   
590  154.812903  150.0  327.0  313.400000  299.0   13.6  13.393548   13.2   
591  154.777419  147.7  326.0  313.472727  298.0   13.6  13.400000   13.2   
593  155.438710  149.0  327.0  313.363636  298.0   13.6  13.351613   13.2   
597  167.087097  161.1  326.0  304.818182  289.0   13.6  13.380000   13.2   

     HOUR  DAY_OF_WEEK  
22      8            2  
23      9            2  
25      9            7  
29     23            7  
37      3            3  
..    ...          ...  
589    18            2  
590     1            3  
591     1            3  
593    14            4  
597    14            4  

[349 rows x 667 columns]

In [186]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...      X_926  \
0     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.962572   
1     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -45.815738   
2     0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.022073   
3     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.606526   
4     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.544146   
..    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...        ...   
344  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.092131   
345  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.241843   
346  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.231286   
347   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.428023   
348  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...   3.893474   

     X_927  X_928      X_929      X_930  X_931       X_932  X_933      HOUR  \
0     0.66    0.0   0.386364   0.111111    1.0    0.584058    0.0 -0.166667   
1   -29.52  -32.6 -38.275000 -32.111111 -136.0 -180.608692  -13.2 -0.083333   
2     0.66    0.1   0.581818   1.000000    1.0    0.739130    0.0 -0.083333   
3     0.30    0.1   0.738636   1.000000    1.0    0.304348    0.0  1.083333   
4     0.16    0.1   0.756818   1.000000    1.0    0.763768    0.1 -0.583333   
..     ...    ...        ...        ...    ...         ...    ...       ...   
344   0.30    0.0   0.634091   1.000000    1.0    1.130435    0.1  0.666667   
345   0.48    0.1   0.900000   1.111111    0.0   -0.086956    0.0 -0.750000   
346   0.02    0.0   0.909091   1.000000    0.0    0.000000    0.0 -0.750000   
347   0.28    0.1   0.895455   1.000000    0.0   -0.652174    0.0  0.333333   
348   2.70    0.0  -0.172727   0.000000    0.0   -0.269565    0.0  0.333333   

     DAY_OF_WEEK  
0      -1.000000  
1      -1.000000  
2       0.666667  
3       0.666667  
4      -0.666667  
..           ...  
344    -1.000000  
345    -0.666667  
346    -0.666667  
347    -0.333333  
348    -0.333333  

[349 rows x 667 columns]

In [187]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...  \
index                                                           ...   
22      0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
23      0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
25      0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
29      0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
37      0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   
...     ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...   
589    -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   
590    -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   
591    -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   
593     0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   
597    19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...   

           X_926  X_927  X_928      X_929      X_930  X_931       X_932  \
index                                                                     
22      0.962572   0.66    0.0   0.386364   0.111111    1.0    0.584058   
23    -45.815738 -29.52  -32.6 -38.275000 -32.111111 -136.0 -180.608692   
25      0.022073   0.66    0.1   0.581818   1.000000    1.0    0.739130   
29      0.606526   0.30    0.1   0.738636   1.000000    1.0    0.304348   
37      0.544146   0.16    0.1   0.756818   1.000000    1.0    0.763768   
...          ...    ...    ...        ...        ...    ...         ...   
589     0.092131   0.30    0.0   0.634091   1.000000    1.0    1.130435   
590     0.241843   0.48    0.1   0.900000   1.111111    0.0   -0.086956   
591     0.231286   0.02    0.0   0.909091   1.000000    0.0    0.000000   
593     0.428023   0.28    0.1   0.895455   1.000000    0.0   -0.652174   
597     3.893474   2.70    0.0  -0.172727   0.000000    0.0   -0.269565   

       X_933      HOUR  DAY_OF_WEEK  
index                                
22       0.0 -0.166667    -1.000000  
23     -13.2 -0.083333    -1.000000  
25       0.0 -0.083333     0.666667  
29       0.0  1.083333     0.666667  
37       0.1 -0.583333    -0.666667  
...      ...       ...          ...  
589      0.1  0.666667    -1.000000  
590      0.0 -0.750000    -0.666667  
591      0.0 -0.750000    -0.666667  
593      0.0  0.333333    -0.333333  
597      0.0  0.333333    -0.333333  

[349 rows x 667 columns]

In [188]:
T10_data = T10_data.to_numpy()
#T05_target = np.log1p(T05_target)
T10_target = T10_target.to_numpy().reshape(-1, 1)

In [189]:
kf = KFold(n_splits=5, random_state=414, shuffle=True)
predictions_array =[]
CV_score_array    =[]
for train_index, test_index in kf.split(T10_data):
    T10_data_train, T10_data_valid = T10_data[train_index], T10_data[test_index]
    T10_target_train, T10_target_valid = T10_target[train_index], T10_target[test_index]
    T10_regressor = TabNetRegressor(verbose=0, seed=42)
    T10_regressor.fit(X_train=T10_data_train, y_train=T10_target_train,
              eval_set=[(T10_data_valid, T10_target_valid)],
              patience=300, max_epochs=2000,
              eval_metric=['rmse'])
    CV_score_array.append(T10_regressor.best_cost)
    #predictions_array.append(np.expm1(regressor.predict(X_test)))

    print("The CV score is %.5f" % np.mean(CV_score_array,axis=0) )    
#predictions = np.mean(predictions_array,axis=0)


Early stopping occurred at epoch 1039 with best_epoch = 739 and best_val_0_rmse = 0.00641
Best weights from best epoch are automatically used!
The CV score is 0.00641

Early stopping occurred at epoch 329 with best_epoch = 29 and best_val_0_rmse = 0.14215
Best weights from best epoch are automatically used!
The CV score is 0.07428

Early stopping occurred at epoch 1280 with best_epoch = 980 and best_val_0_rmse = 0.00333
Best weights from best epoch are automatically used!
The CV score is 0.05063

Early stopping occurred at epoch 1283 with best_epoch = 983 and best_val_0_rmse = 0.00718
Best weights from best epoch are automatically used!
The CV score is 0.03977

Early stopping occurred at epoch 1171 with best_epoch = 871 and best_val_0_rmse = 0.00543
Best weights from best epoch are automatically used!
The CV score is 0.03290


In [190]:
T10_datas = T10_regressor.predict(T10_data)
T10_datas = pd.DataFrame(T10_datas, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.532213
1     0.907022
2     0.533050
3     0.535409
4     0.535413
..         ...
344   0.534647
345   0.531137
346   0.526404
347   0.530229
348   0.534580

[349 rows x 1 columns]

In [191]:
T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')
T10_datas

Y_Quality
index           
22      0.532213
23      0.907022
25      0.533050
29      0.535409
37      0.535413
...          ...
589     0.534647
590     0.531137
591     0.526404
593     0.530229
597     0.534580

[349 rows x 1 columns]

In [192]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [193]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [194]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [195]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                        criterion='entropy', max_depth=5, max_features='sqrt',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.3, min_samples_leaf=3,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=170, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.0001, loss='deviance', max_depth=1,
                            max_features='sqrt', max_leaf_nodes=None,
                            min_impurity_decrease=0.0005, min_samples_leaf=4,
                            min_samples_split=9, min_weight_fraction_leaf=0.0,
                            n_estimators=270, n_iter_no_change=None,
                            random_state=

In [196]:
for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.8248
245   0.530229        1                 1            0.8248
246   0.532073        1                 1            0.8248
247   0.530751        1                 1            0.8248
248   0.907022        0                 1            0.8248
..         ...      ...               ...               ...
344   0.506570        1                 1            0.8248
345   0.531137        1                 1            0.8248
346   0.535899        0                 1            0.8248
347   0.525679        1                 1            0.8248
348   0.532432        1                 1            0.8248

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.8288
245   0.530229        1                 1            0.8289
246   0.532073        1                 1            0.8289
247   0.530751        1                 1            0.8289
248   0.907022        0                 1            0.8229
..         ...      ...               ...               ...
344   0.506570        1                 1            0.8222
345   0.531137        1                 1            0.8289
346   0.535899        0                 1            0.8266
347   0.525679        1                 1            0.8288
348   0.532432        1                 1            0.8289

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.8248
245   0.530229        1                 1            0.8248
246   0.532073        1                 1            0.8248
247   0.530751        1                 1            0.8248
248   0.907022        0                 1            0.8248
..         ...      ...               ...               ...
344   0.506570        1                 1            0.8248
345   0.531137        1                 1            0.8248
346   0.535899        0                 1            0.8248
347   0.525679        1                 1            0.8248
348   0.532432        1                 1            0.8248

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.3927
245   0.530229        1                 1            0.3943
246   0.532073        1                 1            0.3955
247   0.530751        1                 1            0.3945
248   0.907022        0                 1            0.3807
..         ...      ...               ...               ...
344   0.506570        1                 1            0.3806
345   0.531137        1                 1            0.3956
346   0.535899        0                 1            0.3861
347   0.525679        1                 1            0.3913
348   0.532432        1                 1            0.3950

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.4683
245   0.530229        1                 1            0.4592
246   0.532073        1                 1            0.4934
247   0.530751        1                 1            0.4573
248   0.907022        0                 1            0.4211
..         ...      ...               ...               ...
344   0.506570        1                 1            0.4229
345   0.531137        1                 1            0.4847
346   0.535899        0                 1            0.4626
347   0.525679        1                 1            0.4845
348   0.532432        1                 1            0.4838

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.3494
245   0.530229        1                 1            0.3439
246   0.532073        1                 1            0.3538
247   0.530751        1                 1            0.3417
248   0.907022        0                 1            0.4355
..         ...      ...               ...               ...
344   0.506570        1                 0            0.5345
345   0.531137        1                 1            0.3472
346   0.535899        0                 1            0.3616
347   0.525679        1                 1            0.3575
348   0.532432        1                 1            0.3519

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.527125        1                 1            0.7435
245   0.530229        1                 1            0.7531
246   0.532073        1                 1            0.9833
247   0.530751        1                 1            0.6828
248   0.907022        0                 1            0.6560
..         ...      ...               ...               ...
344   0.506570        1                 1            0.6761
345   0.531137        1                 1            0.9603
346   0.535899        0                 1            0.8065
347   0.525679        1                 1            0.9657
348   0.532432        1                 1            0.7729

[105 rows x 4 columns]

In [197]:
T10_vote_classification_models = [
    ('ada',  T10_model_ada),
    ('lightgbm', T10_model_lightgbm),
    ('rf', T10_model_rf),
    ('gbc', T10_model_gbc),
    ('et', T10_model_et),
    ('cat', T10_model_catboost),
    ('xgb', T10_model_xgb),
]

In [198]:
T10_soft_vote = VotingClassifier(T10_vote_classification_models, voting = 'soft')
#soft_vote_cv = cross_validate(soft_vote, T01_datas, T01_class, cv = KFold)
T10_soft_vote.fit(T10_datas, T10_class)

VotingClassifier(estimators=[('ada',
                              AdaBoostClassifier(algorithm='SAMME.R',
                                                 base_estimator=None,
                                                 learning_rate=1.0,
                                                 n_estimators=50,
                                                 random_state=414)),
                             ('lightgbm',
                              LGBMClassifier(boosting_type='gbdt',
                                             class_weight=None,
                                             colsample_bytree=1.0,
                                             importance_type='split',
                                             learning_rate=0.1, max_depth=-1,
                                             min_child_samples=20,
                                             min_child_weight=0.001,
                                             min_split_gain=0...
                               

In [199]:
T10_prediction = pd.DataFrame(T10_soft_vote.predict(T10_datas), columns = ['prediction_label'])
T10_prediction

prediction_label
0                   1
1                   1
2                   1
3                   1
4                   1
..                ...
344                 1
345                 1
346                 1
347                 1
348                 1

[349 rows x 1 columns]

In [200]:
T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [201]:
T10_prediction

prediction_label
index                  
22                    1
23                    1
25                    1
29                    1
37                    1
...                 ...
589                   1
590                   1
591                   1
593                   1
597                   1

[349 rows x 1 columns]

# Test

In [287]:
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [288]:
test_data['YEAR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.year
test_data['MONTH'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.month
test_data['DAY'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day
test_data['HOUR'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.hour
test_data['MINUTE'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.minute
test_data['DAY_OF_WEEK'] =  pd.to_datetime(test_data['TIMESTAMP']).dt.day_name()

In [289]:
test_data = test_data.drop(['MONTH', 'DAY', 'YEAR', 'MINUTE'], axis = 1)

In [290]:
test_data.drop(colls, inplace = True, axis = 1)

In [291]:
test_data.loc[test_data.DAY_OF_WEEK == 'Monday','DAY_OF_WEEK'] = 1
test_data.loc[test_data.DAY_OF_WEEK == 'Tuesday','DAY_OF_WEEK'] = 2
test_data.loc[test_data.DAY_OF_WEEK == 'Wednesday','DAY_OF_WEEK'] = 3
test_data.loc[test_data.DAY_OF_WEEK == 'Thursday','DAY_OF_WEEK'] = 4
test_data.loc[test_data.DAY_OF_WEEK == 'Friday','DAY_OF_WEEK'] = 5
test_data.loc[test_data.DAY_OF_WEEK == 'Saturday','DAY_OF_WEEK'] = 6
test_data.loc[test_data.DAY_OF_WEEK == 'Sunday','DAY_OF_WEEK'] = 7

test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

         X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
1           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     2   
2           NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN     8   
3    444.192308   423.0     NaN     NaN     NaN     NaN     NaN     NaN    10   
4    443.211539   423.0     NaN     NaN     NaN     NaN     NaN     NaN    11   
..          ...     ...     ...     ...     ...     ...     ...     ...   ...   
305         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    11   
306         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
307         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    16   
308         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    20   
309         NaN     NaN     NaN     NaN     NaN     NaN     NaN     NaN    21   

     DAY_OF_WEEK  
0              5  
1              5  
2              5  
3              5  
4              5  
..           ...  
305            6  
306            6  
307            6  
308            6  
309            6  

[310 rows x 2797 columns]

In [292]:
TT050304 = test_data[test_data['LINE'] == 'T050304']
TT050307 = test_data[test_data['LINE'] == 'T050307']
TT010305 = test_data[test_data['LINE'] == 'T010305']
TT010306 = test_data[test_data['LINE'] == 'T010306']
TT100304 = test_data[test_data['LINE'] == 'T100304']
TT100306 = test_data[test_data['LINE'] == 'T100306']
TT050304

LINE PRODUCT_CODE  X_1  X_2  X_3  X_4  X_5  X_6  X_7  X_8  ...  \
7   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
8   T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
14  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
35  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
41  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
42  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
52  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
53  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
54  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
61  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
64  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
65  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   
66  T050304            1  NaN  NaN  NaN  NaN  NaN  NaN  NaN  NaN  ...   

        X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
7   369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0    12   
8   370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0    12   
14  369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0     6   
35  369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0     3   
41  368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0    23   
42  368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0    23   
52  368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0    17   
53  361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0    17   
54  367.849057   352.0   55.72   57.57   42.08   55.19   66.06     1.0    18   
61  370.000000   354.0     NaN     NaN     NaN     NaN     NaN     1.0    21   
64  367.943396   352.0     NaN     NaN     NaN     NaN     NaN     1.0     0   
65  368.056604   352.0   51.55   55.55   39.85   47.82   61.59     1.0     3   
66  369.111111   353.0   51.37   55.70   52.49   48.34   62.12     1.0     8   

    DAY_OF_WEEK  
7             6  
8             6  
14            6  
35            7  
41            1  
42            1  
52            3  
53            3  
54            3  
61            7  
64            1  
65            1  
66            1  

[13 rows x 2797 columns]

In [293]:
TT050304.drop(['LINE'], axis = 1, inplace = True)
TT050307.drop(['LINE'], axis = 1, inplace = True)
TT010305.drop(['LINE'], axis = 1, inplace = True)
TT010306.drop(['LINE'], axis = 1, inplace = True)
TT100304.drop(['LINE'], axis = 1, inplace = True)
TT100306.drop(['LINE'], axis = 1, inplace = True)

In [294]:
TT050304.drop(T050304_col, inplace = True, axis = 1)
TT050307.drop(T050307_col, inplace = True, axis = 1)
TT010305.drop(T010305_col, inplace = True, axis = 1)
TT010306.drop(T010306_col, inplace = True, axis = 1)
TT100304.drop(T100304_col, inplace = True, axis = 1)
TT100306.drop(T100306_col, inplace = True, axis = 1)
TT050304

PRODUCT_CODE    X_128    X_129  X_132  X_133  X_134  X_135  X_136  X_137  \
7             1  18031.0  18031.0   0.19   0.20   0.19    0.2  354.0  354.0   
8             1  18064.0  18064.0   0.19   0.20   0.19    0.2  355.0  354.0   
14            1    295.0    295.0   0.19   0.21   0.19    0.2   60.0   60.0   
35            1   8632.0   8632.0   0.20   0.21   0.20    0.2  249.0  249.0   
41            1  10712.0  10712.0   0.20   0.21   0.20    0.2  293.0  293.0   
42            1  10729.0  10729.0   0.20   0.21   0.19    0.2  293.0  293.0   
52            1  12261.0  12261.0   0.19   0.21   0.19    0.2  330.0  330.0   
53            1  12283.0  12283.0   0.20   0.21   0.20    0.2  330.0  330.0   
54            1  12305.0  12305.0   0.19   0.21   0.19    0.2  330.0  330.0   
61            1  17990.0  17990.0   0.20   0.21   0.20    0.2  436.0  436.0   
64            1  18026.0  18026.0   0.20   0.21   0.20    0.2  437.0  437.0   
65            1  18220.0  18220.0   0.20   0.21   0.20    0.2  441.0  441.0   
66            1  18514.0  18514.0   0.20   0.21   0.20    0.2  446.0  446.0   

    X_138  ...      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  \
7   354.0  ...  369.462963   354.0   57.74   52.51   54.45   57.99   63.16   
8   355.0  ...  370.259259   353.0   53.18   56.02   41.79   47.94   60.72   
14   60.0  ...  369.377359   353.0   49.77   54.93   49.85   48.62   63.18   
35  249.0  ...  369.660377   352.0   55.22   58.14   48.93   56.16   64.25   
41  293.0  ...  368.018519   352.0   49.67   45.00   49.81   55.19   67.17   
42  293.0  ...  368.452830   353.0   51.30   47.66   60.00   53.75   62.58   
52  330.0  ...  368.320755   353.0   54.06   51.18   52.17   57.75   63.94   
53  330.0  ...  361.226415   342.0   54.04   51.25   54.98   57.22   63.33   
54  330.0  ...  367.849057   352.0   55.72   57.57   42.08   55.19   66.06   
61  436.0  ...  370.000000   354.0     NaN     NaN     NaN     NaN     NaN   
64  437.0  ...  367.943396   352.0     NaN     NaN     NaN     NaN     NaN   
65  441.0  ...  368.056604   352.0   51.55   55.55   39.85   47.82   61.59   
66  446.0  ...  369.111111   353.0   51.37   55.70   52.49   48.34   62.12   

    X_2871  HOUR  DAY_OF_WEEK  
7      1.0    12            6  
8      1.0    12            6  
14     1.0     6            6  
35     1.0     3            7  
41     1.0    23            1  
42     1.0    23            1  
52     1.0    17            3  
53     1.0    17            3  
54     1.0    18            3  
61     1.0    21            7  
64     1.0     0            1  
65     1.0     3            1  
66     1.0     8            1  

[13 rows x 1971 columns]

In [295]:
TT05 = pd.concat([TT050304, TT050307])
TT01 = pd.concat([TT010305, TT010306])
TT10 = pd.concat([TT100304, TT100306])

In [296]:
TT05.drop(T5drop, inplace = True, axis = 1)
TT01.drop(T0drop, inplace = True, axis = 1)
TT10.drop(T1drop, inplace = True, axis = 1)

In [297]:
TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)

In [298]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      14
3      35
4      41
5      42
6      52
7      53
8      54
9      61
10     64
11     65
12     66
13     13
14     36
15     62
16     63
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [299]:
TT05.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [300]:
T_05c = T05_data.columns
T_05scaler = RobustScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

X_132  X_133  X_134  X_135     X_136     X_137     X_138     X_139  \
0     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.024793   
1     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.024793   
2     -1.0   -1.0   -2.0    0.0 -0.199797 -0.201826 -0.208864 -0.008264   
3     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864  0.002755   
4     -1.0   -1.0   -1.0    0.0 -0.199797 -0.201826 -0.208864 -0.002755   
..     ...    ...    ...    ...       ...       ...       ...       ...   
115   -1.0   -1.0   -1.0    0.0 -0.497972 -0.500000 -0.502292 -1.049587   
116   -1.0   -1.0   -1.0    0.0 -0.495943 -0.497972 -0.500255 -1.049587   
117   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.044077   
118   -1.0   -1.0   -1.0    0.0 -0.491886 -0.493915 -0.496179 -1.033058   
119   -1.0   -1.0   -1.0    0.0 -0.485801 -0.487830 -0.490066 -1.082645   

        X_140     X_141  ...    X_2864  X_2865    X_2866    X_2867    X_2868  \
0   -0.052154  0.023437  ...  0.058361     1.0 -0.819981 -0.721628 -1.242857   
1   -0.029478  0.315104  ... -0.511376     1.0 -0.829261 -0.942865 -0.535000   
2   -0.043084 -0.049479  ... -0.493215     0.0 -0.859573 -0.669450 -0.216429   
3   -0.043084 -1.195312  ...  0.134068     1.0 -1.243118 -0.693973 -0.828571   
4   -0.047619  0.263021  ...  3.097439     1.0 -0.639963 -0.602661  0.402857   
..        ...       ...  ...       ...     ...       ...       ...       ...   
115 -0.882086 -0.898437  ... -0.709724    -8.0  0.023198  0.080355  0.227143   
116 -0.891156 -0.929687  ... -3.013162   -10.0  0.000928 -0.084529  0.524286   
117 -0.886621 -0.695312  ...  0.722783     0.0 -0.019487  0.079311  0.322143   
118 -0.877551 -0.919271  ...  0.700745     0.0  0.064646  0.218106 -0.007857   
119 -0.877551 -1.263021  ... -0.665646     1.0 -3.253634 -2.855205 -3.568571   

       X_2869     X_2870  X_2871      HOUR  DAY_OF_WEEK  
0   -0.958879   3.252475    -1.0 -0.222222         -0.6  
1   -0.848622   3.396040    -1.0 -0.222222         -0.6  
2   -1.004067   3.054455    -1.0 -0.222222         -0.6  
3   -1.106191   3.044554    -1.0 -0.111111         -0.6  
4   -0.996385   3.433168    -1.0 -0.111111         -0.6  
..        ...        ...     ...       ...          ...  
115  0.044736   0.346535     0.0  0.111111          0.2  
116  0.057840   0.544554     0.0  0.111111          0.2  
117 -0.214641  -0.519802     0.0  0.222222          0.2  
118  0.106191  -0.368812     0.0  0.777778          0.2  
119 -2.499322 -15.997525     0.0  0.555556          0.2  

[120 rows x 1958 columns]

In [301]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

X_132  X_133  X_134  X_135  X_136  X_137  X_138  X_139  X_140  X_141  ...  \
0    0.19   0.20   0.19    0.2  354.0  354.0  354.0  591.5  597.7  575.6  ...   
1    0.19   0.20   0.19    0.2  355.0  354.0  355.0  591.5  597.7  575.7  ...   
2    0.19   0.21   0.19    0.2   60.0   60.0   60.0  558.4  561.9  547.5  ...   
3    0.20   0.21   0.20    0.2  249.0  249.0  249.0  583.1  587.1  569.9  ...   
4    0.20   0.21   0.20    0.2  293.0  293.0  293.0  580.9  585.1  570.4  ...   
5    0.20   0.21   0.19    0.2  293.0  293.0  293.0  581.0  585.2  568.9  ...   
6    0.19   0.21   0.19    0.2  330.0  330.0  330.0  582.9  587.9  542.4  ...   
7    0.20   0.21   0.20    0.2  330.0  330.0  330.0  583.4  588.0  563.9  ...   
8    0.19   0.21   0.19    0.2  330.0  330.0  330.0  583.0  587.8  570.4  ...   
9    0.20   0.21   0.20    0.2  436.0  436.0  436.0  592.1  597.9  580.8  ...   
10   0.20   0.21   0.20    0.2  437.0  437.0  437.0  593.7  599.4  580.1  ...   
11   0.20   0.21   0.20    0.2  441.0  441.0  441.0  593.8  599.7  574.6  ...   
12   0.20   0.21   0.20    0.2  446.0  446.0  446.0  593.2  599.0  583.9  ...   
13   0.21   0.22   0.21    0.2  230.0  230.0  231.0  580.6  584.1  562.0  ...   
14   0.21   0.22   0.21    0.2   99.0   99.0   99.0  581.5  585.0  569.8  ...   
15   0.21   0.22   0.21    0.2   50.0   49.0   40.0  578.6  582.2  564.3  ...   
16   0.21   0.22   0.21    0.2   52.0   51.0   41.0  580.5  584.0  569.5  ...   
17   0.21   0.22   0.20    0.2  424.0  423.0  413.0  585.7  591.2  573.0  ...   
18   0.21   0.21   0.21    0.2  424.0  423.0  414.0  584.4  590.1  565.8  ...   
19   0.21   0.22   0.21    0.2  426.0  425.0  416.0  584.2  589.5  569.1  ...   
20   0.21   0.22   0.21    0.2  732.0  731.0  722.0  595.5  602.0  577.2  ...   
21   0.21   0.22   0.21    0.2  732.0  731.0  722.0  594.8  601.4  573.3  ...   
22   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.0  600.8  556.5  ...   
23   0.21   0.22   0.21    0.2  733.0  732.0  722.0  594.1  600.8  578.3  ...   
24   0.21   0.22   0.21    0.2  733.0  732.0  722.0  593.9  600.7  573.7  ...   
25   0.21   0.22   0.21    0.2  733.0  732.0  723.0  594.0  600.8  575.2  ...   
26   0.21   0.22   0.21    0.2  737.0  736.0  727.0  594.4  601.4  567.4  ...   
27   0.21   0.22   0.21    0.2  738.0  737.0  727.0  594.6  601.4  574.3  ...   
28   0.21   0.22   0.20    0.2  738.0  737.0  728.0  595.7  602.5  559.8  ...   
29   0.20   0.22   0.20    0.2  741.0  740.0  730.0  597.0  604.0  583.3  ...   
30   0.21   0.22   0.21    0.2  789.0  788.0  779.0  602.1  608.5  580.6  ...   
31   0.21   0.22   0.21    0.2  790.0  789.0  779.0  600.7  607.3  578.2  ...   
32   0.21   0.22   0.21    0.2  800.0  799.0  789.0  599.7  606.3  582.0  ...   
33   0.21   0.22   0.21    0.2  800.0  799.0  790.0  599.4  606.2  576.2  ...   
34   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.4  606.4  582.6  ...   
35   0.21   0.22   0.21    0.2  806.0  805.0  796.0  599.6  606.4  582.3  ...   
36   0.21   0.22   0.21    0.2  807.0  806.0  796.0  599.6  606.4  575.5  ...   
37   0.21   0.22   0.21    0.2  821.0  820.0  810.0  601.5  608.1  587.5  ...   
38   0.21   0.22   0.21    0.2  821.0  820.0  811.0  601.4  608.1  584.8  ...   

        X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  HOUR  \
0   369.462963   354.0   57.74   52.51   54.45   57.99   63.16     1.0  12.0   
1   370.259259   353.0   53.18   56.02   41.79   47.94   60.72     1.0  12.0   
2   369.377359   353.0   49.77   54.93   49.85   48.62   63.18     1.0   6.0   
3   369.660377   352.0   55.22   58.14   48.93   56.16   64.25     1.0   3.0   
4   368.018519   352.0   49.67   45.00   49.81   55.19   67.17     1.0  23.0   
5   368.452830   353.0   51.30   47.66   60.00   53.75   62.58     1.0  23.0   
6   368.320755   353.0   54.06   51.18   52.17   57.75   63.94     1.0  17.0   
7   361.226415   342.0   54.04   51.25   54.98   57.22   63.33     1.0  17.0   
8   367.849057   352.0   55.72   57.57   42

In [302]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

In [303]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       6
2      10
3      11
4      38
5      40
6      71
7      86
8      88
9      89
10    116
11    117
12    141
13    142
14      4
15      5
16      9
17     12
18     37
19     39
20     72
21     79
22     87
23    109
24    114
25    115
26    128
27    129

In [304]:
TT01.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [305]:
T_01c = T01_data.columns
T_01scaler = RobustScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

X_246  X_247     X_248  X_249  X_250     X_251  X_252  X_253  X_254  \
0      0.0  -0.25 -0.054348    0.0    0.0  1.011236    0.0   -1.0   -1.0   
1      0.0   1.25 -0.054348    0.0    0.0  1.101124    0.0   -1.0   -1.0   
2      0.0   1.25 -0.054348    0.0    0.0  1.146067    0.0    0.0   -1.0   
3      0.0   1.25 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
4      0.0  -0.75 -0.054348    0.0    0.0  1.179775    0.0   -1.0   -1.0   
..     ...    ...       ...    ...    ...       ...    ...    ...    ...   
124    0.0   0.75  1.108696    0.0    0.0  0.000000    0.0    0.0    0.0   
125    1.0   1.25  1.293478    0.0    0.0  0.000000    0.0    0.0    0.0   
126    0.0  -0.25  1.423913    0.0    1.0  0.000000    0.0    0.0    0.0   
127    0.0   0.00  1.489130    0.0    0.0  0.000000    0.0    0.0    0.0   
128    0.0   0.75  0.630435    0.0    1.0  0.000000    0.0    0.0    0.0   

     X_255  ...    X_2858    X_2859    X_2860    X_2861    X_2862  X_2863  \
0      0.0  ... -0.390876  0.000000 -0.053030  0.321839  0.041096    -1.9   
1      0.0  ... -0.287500 -0.222798 -0.530303 -0.217241 -0.109589    -1.9   
2      0.0  ... -1.014237 -0.621762  0.106061  0.217816  0.404110    -1.8   
3      0.0  ... -0.542842 -1.191710  0.689394  0.663885  0.595890    -1.9   
4      0.0  ... -1.034646 -1.492228 -0.022727 -0.040517  0.205479    -1.9   
..     ...  ...       ...       ...       ...       ...       ...     ...   
124    0.0  ...  0.285900  0.093264  0.045455 -0.109329 -0.390411    -0.9   
125    0.0  ...  0.550583 -0.134715  0.371212  0.939778  1.041096     0.1   
126    0.0  ...  0.387683  0.424870  0.492424  0.902874  0.876712     0.1   
127    0.0  ...  0.101173  0.279793  0.750000  1.195135  0.910959     0.1   
128    0.0  ...  1.045072  1.056995  0.719697  1.377586  1.150685     0.7   

       X_2864  X_2865      HOUR  DAY_OF_WEEK  
0   -1.452964    -5.0  0.777778     0.666667  
1   -1.500816    -5.0 -0.666667    -1.000000  
2   -1.666123    -8.0 -1.000000    -0.666667  
3   -1.604342    -5.0 -0.111111    -0.666667  
4   -1.524742    -8.5 -0.111111    -0.666667  
..        ...     ...       ...          ...  
124 -0.482871    -5.0  0.222222    -1.000000  
125  0.344334     1.0  0.222222     0.000000  
126  0.264525     0.0 -0.333333     0.666667  
127  0.428577     2.0  0.222222    -1.333333  
128  0.924415     4.5 -0.222222    -1.333333  

[129 rows x 880 columns]

In [306]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  ...  \
0     1.0   93.0    0.0   45.0   11.0   37.0   45.0   11.0   42.0    2.0  ...   
1     1.0   93.0    0.0   45.0   11.0   40.0   45.0   11.0   42.0    2.0  ...   
2     1.0   90.0    0.0   45.0   11.0   46.0   45.0   11.0   42.0    2.0  ...   
3     1.0   95.0    0.0   45.0   11.0   53.0   45.0   11.0   42.0    2.0  ...   
4     2.0   88.0    0.0   45.0   11.0  134.0   45.0   11.0   42.0    2.0  ...   
5     2.0   93.0    0.0   45.0   11.0  141.0   45.0   11.0   42.0    2.0  ...   
6     2.0   89.0    0.0   45.0   11.0    6.0   45.0   11.0   42.0    2.0  ...   
7     1.0   89.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0  ...   
8    17.0   90.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0  ...   
9     2.0   89.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0  ...   
10    2.0   90.0    0.0   45.0   11.0   43.0   45.0   11.0   42.0    2.0  ...   
11    1.0   88.0    0.0   45.0   11.0   43.0   45.0   11.0   42.0    2.0  ...   
12    1.0   88.0    0.0   45.0   11.0   69.0   45.0   11.0   42.0    2.0  ...   
13    2.0   87.0    0.0   45.0   11.0   69.0   45.0   12.0   42.0    2.0  ...   
14    2.0   95.0   89.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
15    2.0   90.0   92.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
16    1.0   89.0   98.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0  ...   
17    2.0   89.0  105.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0  ...   
18    1.0   94.0   14.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
19    2.0   91.0   21.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
20    2.0   97.0   88.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
21    1.0   90.0   93.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
22    1.0   92.0  111.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
23    4.0   97.0  127.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
24    1.0   95.0  130.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
25    2.0   93.0  130.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
26    1.0   95.0  143.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   
27    2.0   93.0  143.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0  ...   

        X_2858  X_2859  X_2860      X_2861  X_2862  X_2863      X_2864  \
0   179.739286   149.9   198.0  191.450000   183.8   467.0  444.192308   
1   162.317241   120.6   201.5  194.351724   175.1   464.0  445.075472   
2   174.050000   159.7   198.6  189.853571   174.4   466.0  444.115385   
3   167.950000   146.8   197.1  187.360714   176.1   466.0  444.230769   
4   158.975862   133.1   195.3  187.644828   180.1   462.0  447.962264   
5   167.382759   143.7   204.2  197.510345   185.7   466.0  450.622641   
6   182.293103   165.1   202.4  196.879310   187.1   465.0  444.792453   
7   189.627586   161.8   202.4  196.593103   179.9   466.0  448.490566   
8   274.425000   246.0   226.6  217.092857   206.3   466.0  442.480769   
9   193.364286   175.9   201.8  197.789286   184.3   465.0  445.711539   
10  167.203571   126.1   201.4  193.889286   182.7   466.0  446.826923   
11  160.089655   139.6   205.8  195.703448   189.0   456.0  440.792453   
12  230.879310   201.1   205.5  196.948276   190.4   466.0  444.584906   
13  239.992857   224.4   215.5  205.421429   195.7   466.0  448.423077   
14  190.664286   162.4   210.2  193.082143   179.7   465.0  443.211539   
15  170.910345   148.9   203.3  192.375862   181.7   466.0  441.830189   
16  187.675000   177.9   197.0  192.400000   184.5   456.0  439.596154   
17  170.813793   151.9   197.1  191.003448   186.2   466.0  449.226415   
18  184.132143   159.2   197.3  187.028571   172.8   466.0  445.384615   
19  162.955172   135.9   206.8  198.848276   187.0   475.0  454.924528   
20  183.989655   143.2   206.1  197.572414   179.1   466.0  443.207547   
21  171.996552   142.2   2

In [307]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  X_254  X_255  \
index                                                                         
3        1.0   93.0    0.0   45.0   11.0   37.0   45.0   11.0   42.0    2.0   
6        1.0   93.0    0.0   45.0   11.0   40.0   45.0   11.0   42.0    2.0   
10       1.0   90.0    0.0   45.0   11.0   46.0   45.0   11.0   42.0    2.0   
11       1.0   95.0    0.0   45.0   11.0   53.0   45.0   11.0   42.0    2.0   
38       2.0   88.0    0.0   45.0   11.0  134.0   45.0   11.0   42.0    2.0   
40       2.0   93.0    0.0   45.0   11.0  141.0   45.0   11.0   42.0    2.0   
71       2.0   89.0    0.0   45.0   11.0    6.0   45.0   11.0   42.0    2.0   
86       1.0   89.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0   
88      17.0   90.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0   
89       2.0   89.0    0.0   45.0   11.0   23.0   45.0   11.0   42.0    2.0   
116      2.0   90.0    0.0   45.0   11.0   43.0   45.0   11.0   42.0    2.0   
117      1.0   88.0    0.0   45.0   11.0   43.0   45.0   11.0   42.0    2.0   
141      1.0   88.0    0.0   45.0   11.0   69.0   45.0   11.0   42.0    2.0   
142      2.0   87.0    0.0   45.0   11.0   69.0   45.0   12.0   42.0    2.0   
4        2.0   95.0   89.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
5        2.0   90.0   92.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
9        1.0   89.0   98.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
12       2.0   89.0  105.0   45.0   11.0    0.0   45.0   12.0   51.0    2.0   
37       1.0   94.0   14.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
39       2.0   91.0   21.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
72       2.0   97.0   88.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
79       1.0   90.0   93.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
87       1.0   92.0  111.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
109      4.0   97.0  127.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
114      1.0   95.0  130.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
115      2.0   93.0  130.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
128      1.0   95.0  143.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   
129      2.0   93.0  143.0   45.0   12.0    0.0   45.0   12.0   51.0    2.0   

       ...      X_2858  X_2859  X_2860      X_2861  X_2862  X_2863  \
index  ...                                                           
3      ...  179.739286   149.9   198.0  191.450000   183.8   467.0   
6      ...  162.317241   120.6   201.5  194.351724   175.1   464.0   
10     ...  174.050000   159.7   198.6  189.853571   174.4   466.0   
11     ...  167.950000   146.8   197.1  187.360714   176.1   466.0   
38     ...  158.975862   133.1   195.3  187.644828   180.1   462.0   
40     ...  167.382759   143.7   204.2  197.510345   185.7   466.0   
71     ...  182.293103   165.1   202.4  196.879310   187.1   465.0   
86     ...  189.627586   161.8   202.4  196.593103   179.9   466.0   
88     ...  274.425000   246.0   226.6  217.092857   206.3   466.0   
89     ...  193.364286   175.9   201.8  197.789286   184.3   465.0   
116    ...  167.203571   126.1   201.4  193.889286   182.7   466.0   
117    ...  160.089655   139.6   205.8  195.703448   189.0   456.0   
141    ...  230.879310   201.1   205.5  196.948276   190.4   466.0   
142    ...  239.992857   224.4   215.5  205.421429   195.7   466.0   
4      ...  190.664286   162.4   210.2  193.082143   179.7   465.0   
5      ...  170.910345   148.9   203.3  192.375862   181.7   466.0   
9      ...  187.675000   177.9   197.0  192.400000   184.5   456.0   
12     ...  170.813793   151.9   197.1  191.003448   186.2   466.0   
37     ...  184.132143   159.2   197.3  187.028571   172.8   466.0   
39     ...  162.955172   135.9   206.8  198.848276   187.0   475.0   
72     ...  183.989655   143.2   206.1  197.572414   179.1   466.0   
79     ...  171.996552   1

In [308]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        1
1        2
2       15
3       17
4       20
..     ...
238    301
239    305
240    307
241    308
242    309

[243 rows x 1 columns]

In [309]:
TT10.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [310]:
T_10c = T10_data.columns
T_10scaler = RobustScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

X_1  X_2  X_3  X_4  X_5  X_6       X_7  X_8  X_9  X_10  ...      X_926  \
0     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.962572   
1     0.0  1.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ... -45.815738   
2     0.0  0.4  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.022073   
3     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.606526   
4     0.0  1.0  0.0  0.0  1.0  0.0  0.000000  0.0  0.0   0.0  ...   0.544146   
..    ...  ...  ...  ...  ...  ...       ...  ...  ...   ...  ...        ...   
344  -1.0 -0.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.092131   
345  -1.0 -1.2  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.241843   
346  -1.0 -1.6  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.231286   
347   0.0  0.0  0.0  0.0  0.0  0.0  0.833333  0.0  1.0   0.0  ...   0.428023   
348  19.0 -1.6  0.0  0.0  0.0  0.0  2.666667  0.0  1.0   0.0  ...   3.893474   

     X_927  X_928      X_929      X_930  X_931       X_932  X_933      HOUR  \
0     0.66    0.0   0.386364   0.111111    1.0    0.584058    0.0 -0.166667   
1   -29.52  -32.6 -38.275000 -32.111111 -136.0 -180.608692  -13.2 -0.083333   
2     0.66    0.1   0.581818   1.000000    1.0    0.739130    0.0 -0.083333   
3     0.30    0.1   0.738636   1.000000    1.0    0.304348    0.0  1.083333   
4     0.16    0.1   0.756818   1.000000    1.0    0.763768    0.1 -0.583333   
..     ...    ...        ...        ...    ...         ...    ...       ...   
344   0.30    0.0   0.634091   1.000000    1.0    1.130435    0.1  0.666667   
345   0.48    0.1   0.900000   1.111111    0.0   -0.086956    0.0 -0.750000   
346   0.02    0.0   0.909091   1.000000    0.0    0.000000    0.0 -0.750000   
347   0.28    0.1   0.895455   1.000000    0.0   -0.652174    0.0  0.333333   
348   2.70    0.0  -0.172727   0.000000    0.0   -0.269565    0.0  0.333333   

     DAY_OF_WEEK  
0      -1.000000  
1      -1.000000  
2       0.666667  
3       0.666667  
4      -0.666667  
..           ...  
344    -1.000000  
345    -0.666667  
346    -0.666667  
347    -0.333333  
348    -0.333333  

[349 rows x 667 columns]

In [311]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  \
0    2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
1    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
2    2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
3    2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
4    2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
..   ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...   
238  2.0   94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
239  2.0   91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
240  2.0   91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
241  2.0   95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
242  2.0   87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   

          X_926  X_927  X_928       X_929  X_930  X_931      X_932  X_933  \
0    148.177419  141.4  327.0  312.600000  298.0   13.6  13.406452   13.2   
1    158.951613  157.1  326.0  306.327273  289.0   13.6  13.370968   13.2   
2    162.477419  152.6  317.0  303.454545  289.0   13.6  13.387097   13.2   
3    166.164516  152.6  326.0  310.127273  289.0   13.7  13.403226   13.2   
4    165.248387  159.1  317.0  303.854546  289.0   13.6  13.403333   13.2   
..          ...    ...    ...         ...    ...    ...        ...    ...   
238  151.116129  148.5  327.0  312.745454  298.0   13.6  13.380645   13.2   
239  152.251613  142.9  326.0  313.072727  294.0   13.6  13.341935   13.2   
240  150.909677  145.0  323.0  304.418182  289.0   13.6  13.361290   13.2   
241  153.073333  141.9  326.0  307.018182  290.0   13.6  13.335484   13.2   
242  152.412903  147.1  327.0  308.163636  289.0   13.6  13.343333   13.2   

     HOUR  DAY_OF_WEEK  
0     2.0          5.0  
1     8.0          5.0  
2     5.0          2.0  
3    23.0          4.0  
4     1.0          5.0  
..    ...          ...  
238  15.0          5.0  
239  11.0          6.0  
240  16.0          6.0  
241  20.0          6.0  
242  21.0          6.0  

[243 rows x 667 columns]

In [312]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  X_10  ...  \
index                                                            ...   
1      2.0   93.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
2      2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
15     2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
17     2.0   95.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
20     2.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0   2.0  ...   
...    ...    ...  ...   ...   ...  ...   ...   ...   ...   ...  ...   
301    2.0   94.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
305    2.0   91.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
307    2.0   91.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0   2.0  ...   
308    2.0   95.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   
309    2.0   87.0  0.0  45.0  10.0  0.0  51.0  10.0  52.0   2.0  ...   

            X_926  X_927  X_928       X_929  X_930  X_931      X_932  X_933  \
index                                                                         
1      148.177419  141.4  327.0  312.600000  298.0   13.6  13.406452   13.2   
2      158.951613  157.1  326.0  306.327273  289.0   13.6  13.370968   13.2   
15     162.477419  152.6  317.0  303.454545  289.0   13.6  13.387097   13.2   
17     166.164516  152.6  326.0  310.127273  289.0   13.7  13.403226   13.2   
20     165.248387  159.1  317.0  303.854546  289.0   13.6  13.403333   13.2   
...           ...    ...    ...         ...    ...    ...        ...    ...   
301    151.116129  148.5  327.0  312.745454  298.0   13.6  13.380645   13.2   
305    152.251613  142.9  326.0  313.072727  294.0   13.6  13.341935   13.2   
307    150.909677  145.0  323.0  304.418182  289.0   13.6  13.361290   13.2   
308    153.073333  141.9  326.0  307.018182  290.0   13.6  13.335484   13.2   
309    152.412903  147.1  327.0  308.163636  289.0   13.6  13.343333   13.2   

       HOUR  DAY_OF_WEEK  
index                     
1       2.0          5.0  
2       8.0          5.0  
15      5.0          2.0  
17     23.0          4.0  
20      1.0          5.0  
...     ...          ...  
301    15.0          5.0  
305    11.0          6.0  
307    16.0          6.0  
308    20.0          6.0  
309    21.0          6.0  

[243 rows x 667 columns]

In [280]:
TT05 = TT05.to_numpy()
TT01 = TT01.to_numpy()
TT10 = TT10.to_numpy()

In [281]:
TT05_prediction = T05_regressor.predict(TT05)
TT01_prediction = T01_regressor.predict(TT01)
TT10_prediction = T10_regressor.predict(TT10)

In [313]:
TT05_prediction = pd.DataFrame(TT05_prediction, columns = ['prediction_label'])
TT01_prediction = pd.DataFrame(TT01_prediction, columns = ['prediction_label'])
TT10_prediction = pd.DataFrame(TT10_prediction, columns = ['prediction_label'])
TT05_prediction

prediction_label
0           0.508102
1           0.506621
2           0.533197
3           0.526838
4           0.530113
5           0.531358
6           0.532613
7           0.530670
8           0.531997
9           0.587815
10          0.537165
11          0.547274
12          0.594060
13          0.531949
14          0.500745
15          0.497054
16          0.529413
17          0.533763
18          0.541255
19          0.543015
20          0.523574
21          0.521418
22          0.523575
23          0.527689
24          0.525778
25          0.522547
26          0.528020
27          0.528530
28          0.540605
29          0.484981
30          0.522025
31          0.524836
32          0.512615
33          0.510305
34          0.494257
35          0.538235
36          0.503938
37          0.536567
38          0.494477

In [314]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05_prediction

prediction_label
index                  
7              0.508102
8              0.506621
14             0.533197
35             0.526838
41             0.530113
42             0.531358
52             0.532613
53             0.530670
54             0.531997
61             0.587815
64             0.537165
65             0.547274
66             0.594060
13             0.531949
36             0.500745
62             0.497054
63             0.529413
130            0.533763
131            0.541255
132            0.543015
248            0.523574
249            0.521418
250            0.523575
251            0.527689
252            0.525778
253            0.522547
254            0.528020
255            0.528530
260            0.540605
263            0.484981
280            0.522025
281            0.524836
282            0.512615
283            0.510305
284            0.494257
285            0.538235
286            0.503938
292            0.536567
293            0.494477

In [315]:
TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [316]:
TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [318]:
from pycaret.classification import *

In [319]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])


In [320]:
TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')


In [321]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])


In [322]:
TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')


In [323]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])


In [324]:
TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')


In [325]:
TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

NameError: name 'T05_final_classification_model' is not defined

In [326]:
TT05_predictions = T05_soft_vote.predict(TT05_datas)
TT01_predictions = T01_soft_vote.predict(TT01_datas)
TT10_predictions = T10_soft_vote.predict(TT10_datas)
TT05_predictions = pd.DataFrame(TT05_predictions, columns = ['prediction_label'])
TT01_predictions = pd.DataFrame(TT01_predictions, columns = ['prediction_label'])
TT10_predictions = pd.DataFrame(TT10_predictions, columns = ['prediction_label'])

In [327]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')
TT05_predictions

prediction_label
index                  
7                     1
8                     1
14                    0
35                    1
41                    0
42                    1
52                    0
53                    1
54                    0
61                    2
64                    1
65                    2
66                    0
13                    0
36                    0
62                    0
63                    0
130                   1
131                   2
132                   2
248                   1
249                   0
250                   1
251                   0
252                   1
253                   1
254                   0
255                   0
260                   2
263                   0
280                   0
281                   1
282                   0
283                   0
284                   0
285                   2
286                   0
292                   1
293                   0

In [328]:
TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')
TT01_predictions

prediction_label
index                  
3                     1
6                     1
10                    1
11                    1
38                    1
40                    1
71                    1
86                    1
88                    1
89                    1
116                   1
117                   1
141                   1
142                   1
4                     1
5                     1
9                     1
12                    1
37                    1
39                    1
72                    1
79                    1
87                    1
109                   1
114                   1
115                   1
128                   1
129                   1

In [329]:
TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')
TT10_predictions

prediction_label
index                  
1                     1
2                     1
15                    1
17                    1
20                    1
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[243 rows x 1 columns]

In [330]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

prediction_label
index                  
7                     1
8                     1
14                    0
35                    1
41                    0
...                 ...
301                   1
305                   1
307                   1
308                   1
309                   1

[310 rows x 1 columns]

In [331]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      1
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int64

In [332]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_otherdrop_robust_tabnet_classpyc_fill0_voting_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        1
4   TEST_004        1

In [333]:
final_test['prediction_label'].value_counts()

1    284
0     20
2      6
Name: prediction_label, dtype: int64

In [334]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 0, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 1, 1, 1, 1, 2, 0, 0, 1, 2,
       0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2,
       2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 1, 1, 0, 0, 1, 1, 1, 1, 2, 1, 1, 0,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0, 0, 2,
       0, 1, 1, 1, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1,